In [1]:
import os
import subprocess
import pandas as pd
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
import scipy
import requests
from imdbpie import Imdb
import nltk
import matplotlib.pyplot as plt
import urllib2
from bs4 import BeautifulSoup
import nltk
import collections
import re
import csv

%matplotlib inline

In [2]:
imdb = Imdb()
imdb = Imdb(anonymize=True)

In [2]:
#imdb.top_250()

In [4]:
movies = []
for dct in imdb.top_250():
    del dct['image']
    movies.append(dct)

In [6]:
Can_rate = []
Vote = []
Rate = []
ID = []
Year = []
Title = []
Type = []
for dct in movies:
    Vote.append(dct['num_votes'])
    Rate.append(dct['rating'])
    ID.append(dct['tconst'])
    Year.append(dct['year'])
    Title.append(dct['title'])
    Can_rate.append(dct['can_rate'])
    Type.append(dct['type'])

In [7]:
df = pd.DataFrame({
        "ID": ID,
        'Title': Title,
        'Year': Year,
        'Vote': Vote,
        'Rate': Rate,
        "Can_rate": Can_rate,
        'Type': Type
    })

In [8]:
df.Type.value_counts()

feature    250
Name: Type, dtype: int64

In [9]:
df.Can_rate.value_counts()

True    250
Name: Can_rate, dtype: int64

In [10]:
# Delete 'Can_rate' and 'Type' column coz all rows are same
df.drop('Can_rate',axis=1,inplace=True)
df.drop('Type',axis=1,inplace=True)

In [101]:
#### To save Top_250 movies into csv
df.to_csv('top_movies.csv',encoding='utf-8')

In [66]:
id_list = list(df.ID)

In [70]:
comments = [[] for i in range(250)]
author_score = [[] for i in range(250)]

In [72]:
for i in id_list:
    url = 'http://www.imdb.com/title/' + i + '/' + 'reviews?start=0' 
    contents = BeautifulSoup(urllib2.urlopen(url),"lxml")
    content = contents.find('div',attrs={'class':'reviews'})
    text = contents.find('td',attrs={'align':'right'}).getText()
    n = int(text[1:text.index('r')].strip()) + 10
    for p in range(0,n,10):
        # comments
        url = 'http://www.imdb.com/title/' + i + '/' + 'reviews?start=' + str(p) 
        contents = BeautifulSoup(urllib2.urlopen(url),"lxml")
        content = contents.find('div',attrs={'id':'tn15content'})
        review = content.find_all('p')
        for rew in review:
            comments[id_list.index(i)].append(rew.text) 
        # uid and stars
        
        for user in content.find_all('div'):
            for a in user.find_all('a',href=True)[:1]:
                author_score[id_list.index(i)].append(a.get("href"))
                for img in user.find_all('img', alt=True):
                    author_score[id_list.index(i)].append(img.get('alt'))


    print '# '+str(id_list.index(i)+1) + ' finished'


# 1 finished
# 2 finished
# 3 finished
# 4 finished
# 5 finished
# 6 finished
# 7 finished
# 8 finished
# 9 finished
# 10 finished
# 11 finished
# 12 finished
# 13 finished
# 14 finished
# 15 finished
# 16 finished
# 17 finished
# 18 finished
# 19 finished
# 20 finished
# 21 finished
# 22 finished
# 23 finished
# 24 finished
# 25 finished
# 26 finished
# 27 finished
# 28 finished
# 29 finished
# 30 finished
# 31 finished
# 32 finished
# 33 finished
# 34 finished
# 35 finished
# 36 finished
# 37 finished
# 38 finished
# 39 finished
# 40 finished
# 41 finished
# 42 finished
# 43 finished
# 44 finished
# 45 finished
# 46 finished
# 47 finished
# 48 finished
# 49 finished
# 50 finished
# 51 finished
# 52 finished
# 53 finished
# 54 finished
# 55 finished
# 56 finished
# 57 finished
# 58 finished
# 59 finished
# 60 finished
# 61 finished
# 62 finished
# 63 finished
# 64 finished
# 65 finished
# 66 finished
# 67 finished
# 68 finished
# 69 finished
# 70 finished
# 71 finished
# 72 finished
#

error: [Errno 54] Connection reset by peer

In [9]:
###### To delete "*** This review may contain spoilers ***" and 'Add another review' in comments
reviews = [[] for i in range(250)]

for comment in comments:
    for s in comment:
        if s != "*** This review may contain spoilers ***" and s != 'Add another review':
            reviews[comments.index(comment)].append(s)
        

In [15]:
##### To split author_score into uid and star 
uid = [[] for i in range(250)]
star = [[] for i in range(250)]

for uss in author_score:
    for i in uss:
        try:
            if i.startswith('/user/') and uss[uss.index(i)+1].startswith('/user/'):
                uid[author_score.index(uss)].append(i)
                star[author_score.index(uss)].append('None')
            elif (i.startswith('/user/')) and uss[uss.index(i)+1].endswith('/10'):
                uid[author_score.index(uss)].append(i)
                star[author_score.index(uss)].append(uss[uss.index(i)+1])
        except IndexError: # catch the error
            uid[author_score.index(uss)].append('error')
            star[author_score.index(uss)].append('error')
            continue

In [19]:
import pickle
with open('reviews','wb') as f:
    pickle.dump(reviews,f)

In [20]:
import pickle
with open('uid','wb') as f:
    pickle.dump(uid,f)

In [21]:
import pickle
with open('star','wb') as f:
    pickle.dump(star,f)

### To transfer data into Pandas DataFrame

In [2]:
import pickle
with open('../../../IMDB_250_Backup/Useless/star','rb') as f:
    star = pickle.load(f)

In [3]:
import pickle
with open('../../../IMDB_250_Backup/Useless/uid','rb') as f:
    uid = pickle.load(f)

In [4]:
uid

[['/user/ur2509775/',
  '/user/ur0997166/',
  '/user/ur1005460/',
  '/user/ur1898687/',
  '/user/ur0094239/',
  '/user/ur1285640/',
  '/user/ur0611718/',
  '/user/ur0257957/',
  '/user/ur0355122/',
  '/user/ur0842118/',
  '/user/ur16117882/',
  '/user/ur0174908/',
  '/user/ur0265899/',
  '/user/ur16161013/',
  '/user/ur0226855/',
  '/user/ur1003471/',
  '/user/ur9365949/',
  '/user/ur20345143/',
  '/user/ur0043337/',
  '/user/ur1532177/',
  '/user/ur24573739/',
  '/user/ur9871443/',
  '/user/ur6657969/',
  '/user/ur31182745/',
  '/user/ur29409681/',
  '/user/ur0138488/',
  '/user/ur8635707/',
  '/user/ur0082617/',
  '/user/ur17447627/',
  '/user/ur0643062/',
  '/user/ur28007261/',
  '/user/ur31638149/',
  '/user/ur1896124/',
  '/user/ur2707735/',
  '/user/ur8503729/',
  '/user/ur23169472/',
  '/user/ur3435249/',
  '/user/ur1926657/',
  '/user/ur13374867/',
  '/user/ur6733088/',
  '/user/ur4648178/',
  '/user/ur63955795/',
  '/user/ur39652385/',
  '/user/ur23639929/',
  '/user/ur2426109

In [12]:

import pickle
with open('../../../IMDB_250_Backup/Useless/reviews','rb') as f:
    reviews = pickle.load(f)
 

In [5]:
df = pd.read_csv('../../../IMDB_250_Backup/top_movies.csv')
id_list = list(df.ID)

In [6]:
# To build star dataframe
total = []
for i in id_list:
    df = pd.DataFrame({i: star[id_list.index(i)]})
    total.append(df)
star = pd.concat(total, axis=1)

In [7]:
star

tt0111161 tt0068646 tt0071562 tt0468569 tt0050083 tt0108052 tt0110912  \
0        10/10     10/10     10/10     10/10     10/10     10/10     10/10   
1        10/10     10/10     10/10     10/10     10/10     10/10     10/10   
2         None     10/10     10/10     10/10      9/10     10/10     10/10   
3        10/10     10/10     10/10     10/10     10/10     10/10     10/10   
4         None     10/10     10/10     10/10      None      None     10/10   
5         8/10      9/10     10/10     10/10     10/10      None      None   
6        10/10     10/10      9/10     10/10      9/10      None     10/10   
7        10/10     10/10     10/10     10/10      None     10/10      None   
8        10/10     10/10     10/10     10/10      8/10     10/10     10/10   
9        10/10     10/10      None     10/10      None      9/10      None   
10       10/10     10/10      None      8/10      None      None      1/10   
11       10/10     10/10     10/10     10/10     10/10      None      2/10   
12       10/10     10/10     10/10      9/10     10/10     10/10      1/10   
13       10/10     10/10     10/10      8/10      7/10     10/10      None   
14        8/10     10/10     10/10     10/10     10/10     10/10      1/10   
15       10/10      8/10     10/10     10/10     10/10     10/10      4/10   
16       10/10      None      9/10      8/10      8/10      9/10      1/10   
17       10/10      9/10      5/10      8/10     10/10      9/10      1/10   
18       10/10      1/10      9/10      7/10     10/10      1/10      1/10   
19        8/10     10/10      7/10     10/10     10/10      1/10      1/10   
20       10/10      8/10      9/10      4/10     10/10      1/10      1/10   
21       10/10     10/10      None      5/10     10/10      1/10      1/10   
22        7/10     10/10      7/10      7/10      6/10      5/10      3/10   
23       10/10      8/10      4/10      6/10     10/10      None      2/10   
24       10/10      6/10     10/10      6/10     10/10      3/10      2/10   
25        7/10     10/10      5/10      5/10      None      1/10      1/10   
26       10/10      None      8/10     10/10      9/10      1/10      1/10   
27        None     10/10     10/10      7/10     10/10      1/10      5/10   
28       10/10     10/10     10/10      3/10     10/10      9/10      6/10   
29        None     10/10     10/10      6/10      8/10     10/10      5/10   
...        ...       ...       ...       ...       ...       ...       ...   
5039       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5040       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5041       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5042       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5043       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5044       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5045       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5046       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5047       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5048       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5049       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5050       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5051       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5052       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5053       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5054       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5055       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5056       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5057       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5058       NaN       NaN   

In [8]:
# To build uid dataframe
total = []
for i in id_list:
    df = pd.DataFrame({i: uid[id_list.index(i)]})
    total.append(df)
uid = pd.concat(total, axis=1)

In [9]:
def fff(x):
    try:
        if np.isnan(x):
            return
    except:
        return x[6:-1]
uid = uid.applymap(fff)

In [10]:
uid

tt0111161   tt0068646   tt0071562   tt0468569   tt0050083   tt0108052  \
0      ur2509775   ur5445669   ur1170042   ur3789453   ur0599605  ur23582121   
1      ur0997166   ur1241331   ur0200644  ur12680645   ur0668851   ur0676300   
2      ur1005460   ur0218695   ur3782370  ur19572672   ur4070806   ur0671533   
3      ur1898687   ur0453228   ur0588991   ur2862626   ur1869824   ur0609312   
4      ur0094239   ur5347756   ur0176092  ur13846894   ur0643062   ur0355979   
5      ur1285640   ur0078412   ur8564485   ur2371300   ur2011184   ur0478810   
6      ur0611718   ur7154267   ur0139258  ur10583368   ur0645286   ur0823877   
7      ur0257957  ur11305442   ur3341647   ur2747265   ur1318549   ur9295399   
8      ur0355122  ur24740649   ur7484735   ur1293485   ur2159966   ur0034784   
9      ur0842118   ur3920272   ur0167590   ur5237888   ur0688559  ur11178723   
10    ur16117882   ur0139258   ur0688559   ur2935472   ur0224144   ur0109471   
11     ur0174908   ur0257957  ur16117882   ur3338050   ur1293485   ur1355003   
12     ur0265899   ur0176092   ur1173088  ur12449122   ur1173088  ur10334028   
13    ur16161013  ur14069613  ur61769570  ur10484813   ur2004984  ur61769570   
14     ur0226855  ur16117882   ur2093818  ur30410767   ur4532636   ur0176092   
15     ur1003471   ur2955724  ur19117722  ur30457408   ur7784552  ur47157208   
16     ur9365949   ur1002035   ur7343974   ur9972684   ur1309701   ur0444549   
17    ur20345143   ur4445210  ur16594740   ur4532636   ur0453068   ur4445210   
18     ur0043337  ur19554372  ur14069613  ur19605227   ur1406078   ur0873680   
19     ur1532177  ur60719256  ur17822437  ur17109012   ur1532177   ur2553650   
20    ur24573739   ur1117555   ur4445210  ur19593602   ur2467618   ur0969700   
21     ur9871443  ur19117722  ur28434708   ur0325792   ur4234119   ur2083081   
22     ur6657969   ur2860723   ur3063013   ur5783901   ur2483625   ur2585304   
23    ur31182745   ur0137908  ur13450780   ur5777618  ur15884207   ur3056788   
24    ur29409681   ur0650255   ur8625456  ur17816293   ur3329978   ur2726231   
25     ur0138488  ur55829419  ur61573371   ur0102677   ur1002035   ur7572818   
26     ur8635707   ur3623568   ur4096477  ur14510819   ur3924830  ur32875947   
27     ur0082617  ur58619890  ur10568754   ur1773414   ur4888011   ur0251593   
28    ur17447627  ur39322301  ur18910568  ur19852960   ur1577474  ur55118090   
29     ur0643062  ur56007669   ur0257957   ur0855231   ur0989035  ur51408860   
...          ...         ...         ...         ...         ...         ...   
5039        None        None        None        None        None        None   
5040        None        None        None        None        None        None   
5041        None        None        None        None        None        None   
5042        None        None        None        None        None        None   
5043        None        None        None        None        None        None   
5044        None        None        None        None        None        None   
5045        None        None        None        None        None        None   
5046        None        None        None        None        None        None   
5047        None        None        None        None        None        None   
5048        None        None        None        None        None        None   
5049        None        None        None        None        None        None   
5050        None        None        None        None        None        None   
5051        None        None        None        None        None        None   
5052        None        None        None        None        None        None   
5053        None        None        None        None        None        None   
5054        None        None        None        None        None        None   
5055        None        None        None        None        None        None   
5056        None        None        None        None        None        None   
5057   

In [13]:
# To build review dataframe
total = []
for i in id_list:
    df = pd.DataFrame({i: reviews[id_list.index(i)]})
    total.append(df)
reviews = pd.concat(total, axis=1)

In [14]:
reviews

tt0111161  \
0     \nWhy do I want to write the 234th comment on ...   
1     \n\nCan Hollywood, usually creating things for...   
2     \n\nI have never seen such an amazing film sin...   
3     \nIn its Oscar year, Shawshank Redemption (wri...   
4     \nThe reason I became a member of this databas...   
5     \n\nI believe that this film is the best story...   
6     \n\nOne of my all time favorites. Shawshank Re...   
7     \n\nOne of the finest films made in recent yea...   
8     \nMisery and Stand By Me were the best adaptat...   
9     \n\nThe Shawshank Redemption is without a doub...   
10    \nThis movie is not your ordinary Hollywood fl...   
11    \n\nWhenever I talk about this movie with my f...   
12    \nI'm trying to save you money; this is the la...   
13    \nThe Shawshank Redemption is written and dire...   
14    \nAt the heart of this extraordinary movie is ...   
15    \n\n**Yes, there are SPOILERS here**This film ...   
16    \nWe have all see movies, comedies, action and...   
17    \nProbably yes, acting was good, plot brillian...   
18    \nThis touching and heart warming film is the ...   
19    \n\nIn recent years the IMDB top 250 movies ha...   
20    \nWhen I saw that the Shawshank Redemption was...   
21    \nA friend of mine listed "The Shawshank Redem...   
22    \nI still can't quite get the enormous reputat...   
23    \nI made my account on IMDb Just to Rate this ...   
24    \nI first saw this film, like many others, by ...   
25    \n\nI was a little surprised at first to see t...   
26    \nLike I did a few years back, you might be he...   
27    \n  This is Tim Robbins best performance ever....   
28    \nThis is the best movie I have ever seen. In ...   
29    \n\nI reviewed this film recently with a speci...   
...                                                 ...   
5039                                                NaN   
5040                                                NaN   
5041                                                NaN   
5042                                                NaN   
5043                                                NaN   
5044                                                NaN   
5045                                                NaN   
5046                                                NaN   
5047                                                NaN   
5048                                                NaN   
5049                                                NaN   
5050                                                NaN   
5051                                                NaN   
5052                                                NaN   
5053                                                NaN   
5054                                                NaN   
5055                                                NaN   
5056                                                NaN   
5057                                                NaN   
5058                                                NaN   
5059                                                NaN   
5060                                                NaN   
5061                                                NaN   
5062                                                NaN   
5063                                                NaN   
5064                                                NaN   
5065                                                NaN   
5066                                                NaN   
5067                                                NaN   
5068                                                NaN   

                                              tt0068646  \
0     \nRather than concentrating on everything that...   
1     \n\nThis is by far the best movie ever to give...   
2     \n\nThe Godfather is one of the few films in w...   
3     \n\n     This movie is strong, good script, gr...   
4     \nThis is a masterpiece. A timeless masterpiec...   
5     \n\nThe Godfather is one of

In [15]:
uid.to_csv('./uid.csv')
star.to_csv('./star.csv')
reviews.to_csv('./reviews.csv', encoding='utf-8')

## To Create dataframe with UID MovieID Rating columns

In [16]:
top = pd.read_csv('top_movies.csv')
id_list = list(top.ID)

uid = pd.read_csv('uid.csv')
star = pd.read_csv('star.csv')
uid = uid.iloc[:,1:]

"""
reviews = pd.read_csv('reviews.csv')
reviews = reviews.iloc[:,1:]
"""
#Convert 10/10, 8/10 .... to 10 and 8...
def fff(x):
    try:
        if x.endswith('/10'):
            return int(x[:x.find('/')])
    except:
        return
star = star.iloc[:,1:].applymap(fff)

//anaconda/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2723: DtypeWarning: Columns (2,3,5,6,7,8,9,10,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,66,67,68,69,70,71,72,73,74,75,76,77,78,79,80,81,82,83,84,85,86,87,88,89,90,91,92,93,94,95,96,97,98,99,100,101,102,103,104,105,106,107,108,109,110,111,112,113,114,115,116,117,118,119,120,121,122,123,124,125,126,127,128,129,130,131,132,133,134,135,136,137,138,139,140,141,142,143,144,145,146,147,148,149,150,151,152,153,154,155,156,157,158,159,160,161,162,163,164,165,166,167,168,169,170,171,172,173,174,175,176,177,178,179,180,181,182,183,184,185,186,187,188,189,190,191,192,193,194,195,196,197,198,199,200,201,202,203,204,205,206,207,208,209,210,211,212,213,214,215,216,217,218,219,220,221,222,223,224,225,226,227,228,229,230,231,232,233,234,235,236,237,238,239,240,241,242,243,244,245,246,247,248,249,250) have mixed ty

In [17]:
5069*250

1267250

In [18]:
# To create MID_UID dataframe
complex_table = pd.DataFrame(columns = ['MID','UID'])
tables = []
for i in id_list:
    table = pd.melt(uid,value_vars=[i],var_name = 'MID', value_name = 'UID')
    tables.append(table)
MID_UID = complex_table.append(tables,ignore_index=True)

In [19]:
MID_UID

MID         UID
0        tt0111161   ur2509775
1        tt0111161   ur0997166
2        tt0111161   ur1005460
3        tt0111161   ur1898687
4        tt0111161   ur0094239
5        tt0111161   ur1285640
6        tt0111161   ur0611718
7        tt0111161   ur0257957
8        tt0111161   ur0355122
9        tt0111161   ur0842118
10       tt0111161  ur16117882
11       tt0111161   ur0174908
12       tt0111161   ur0265899
13       tt0111161  ur16161013
14       tt0111161   ur0226855
15       tt0111161   ur1003471
16       tt0111161   ur9365949
17       tt0111161  ur20345143
18       tt0111161   ur0043337
19       tt0111161   ur1532177
20       tt0111161  ur24573739
21       tt0111161   ur9871443
22       tt0111161   ur6657969
23       tt0111161  ur31182745
24       tt0111161  ur29409681
25       tt0111161   ur0138488
26       tt0111161   ur8635707
27       tt0111161   ur0082617
28       tt0111161  ur17447627
29       tt0111161   ur0643062
...            ...         ...
1267220  tt0169102         NaN
1267221  tt0169102         NaN
1267222  tt0169102         NaN
1267223  tt0169102         NaN
1267224  tt0169102         NaN
1267225  tt0169102         NaN
1267226  tt0169102         NaN
1267227  tt0169102         NaN
1267228  tt0169102         NaN
1267229  tt0169102         NaN
1267230  tt0169102         NaN
1267231  tt0169102         NaN
1267232  tt0169102         NaN
1267233  tt0169102         NaN
1267234  tt0169102         NaN
1267235  tt0169102         NaN
1267236  tt0169102         NaN
1267237  tt0169102         NaN
1267238  tt0169102         NaN
1267239  tt0169102         NaN
1267240  tt0169102         NaN
1267241  tt0169102         NaN
1267242  tt0169102         NaN
1267243  tt0169102         NaN
1267244  tt0169102         NaN
1267245  tt0169102         NaN
1267246  tt0169102         NaN
1267247  tt0169102         NaN
1267248  tt0169102         NaN
1267249  tt0169102         NaN

[1267250 rows x 2 columns]

In [21]:
# To create MID_STAR dataframe
complex_table = pd.DataFrame(columns = ['MID','STAR'])
tables = []
for i in id_list:
    table = pd.melt(star,value_vars=[i],var_name = 'MID', value_name = 'STAR')
    tables.append(table)
MID_STAR = complex_table.append(tables,ignore_index=True)

In [22]:
MID_STAR

MID  STAR
0        tt0111161  10.0
1        tt0111161  10.0
2        tt0111161   NaN
3        tt0111161  10.0
4        tt0111161   NaN
5        tt0111161   8.0
6        tt0111161  10.0
7        tt0111161  10.0
8        tt0111161  10.0
9        tt0111161  10.0
10       tt0111161  10.0
11       tt0111161  10.0
12       tt0111161  10.0
13       tt0111161  10.0
14       tt0111161   8.0
15       tt0111161  10.0
16       tt0111161  10.0
17       tt0111161  10.0
18       tt0111161  10.0
19       tt0111161   8.0
20       tt0111161  10.0
21       tt0111161  10.0
22       tt0111161   7.0
23       tt0111161  10.0
24       tt0111161  10.0
25       tt0111161   7.0
26       tt0111161  10.0
27       tt0111161   NaN
28       tt0111161  10.0
29       tt0111161   NaN
...            ...   ...
1267220  tt0169102   NaN
1267221  tt0169102   NaN
1267222  tt0169102   NaN
1267223  tt0169102   NaN
1267224  tt0169102   NaN
1267225  tt0169102   NaN
1267226  tt0169102   NaN
1267227  tt0169102   NaN
1267228  tt0169102   NaN
1267229  tt0169102   NaN
1267230  tt0169102   NaN
1267231  tt0169102   NaN
1267232  tt0169102   NaN
1267233  tt0169102   NaN
1267234  tt0169102   NaN
1267235  tt0169102   NaN
1267236  tt0169102   NaN
1267237  tt0169102   NaN
1267238  tt0169102   NaN
1267239  tt0169102   NaN
1267240  tt0169102   NaN
1267241  tt0169102   NaN
1267242  tt0169102   NaN
1267243  tt0169102   NaN
1267244  tt0169102   NaN
1267245  tt0169102   NaN
1267246  tt0169102   NaN
1267247  tt0169102   NaN
1267248  tt0169102   NaN
1267249  tt0169102   NaN

[1267250 rows x 2 columns]

In [23]:
# To create MID_STAR_UID dataframe
result = pd.concat([MID_STAR,MID_UID],axis=1,ignore_index=True)
result.columns = ['MID','STAR','MID2','UID']
result.drop('MID2',axis=1,inplace=True)
result

MID  STAR         UID
0        tt0111161  10.0   ur2509775
1        tt0111161  10.0   ur0997166
2        tt0111161   NaN   ur1005460
3        tt0111161  10.0   ur1898687
4        tt0111161   NaN   ur0094239
5        tt0111161   8.0   ur1285640
6        tt0111161  10.0   ur0611718
7        tt0111161  10.0   ur0257957
8        tt0111161  10.0   ur0355122
9        tt0111161  10.0   ur0842118
10       tt0111161  10.0  ur16117882
11       tt0111161  10.0   ur0174908
12       tt0111161  10.0   ur0265899
13       tt0111161  10.0  ur16161013
14       tt0111161   8.0   ur0226855
15       tt0111161  10.0   ur1003471
16       tt0111161  10.0   ur9365949
17       tt0111161  10.0  ur20345143
18       tt0111161  10.0   ur0043337
19       tt0111161   8.0   ur1532177
20       tt0111161  10.0  ur24573739
21       tt0111161  10.0   ur9871443
22       tt0111161   7.0   ur6657969
23       tt0111161  10.0  ur31182745
24       tt0111161  10.0  ur29409681
25       tt0111161   7.0   ur0138488
26       tt0111161  10.0   ur8635707
27       tt0111161   NaN   ur0082617
28       tt0111161  10.0  ur17447627
29       tt0111161   NaN   ur0643062
...            ...   ...         ...
1267220  tt0169102   NaN         NaN
1267221  tt0169102   NaN         NaN
1267222  tt0169102   NaN         NaN
1267223  tt0169102   NaN         NaN
1267224  tt0169102   NaN         NaN
1267225  tt0169102   NaN         NaN
1267226  tt0169102   NaN         NaN
1267227  tt0169102   NaN         NaN
1267228  tt0169102   NaN         NaN
1267229  tt0169102   NaN         NaN
1267230  tt0169102   NaN         NaN
1267231  tt0169102   NaN         NaN
1267232  tt0169102   NaN         NaN
1267233  tt0169102   NaN         NaN
1267234  tt0169102   NaN         NaN
1267235  tt0169102   NaN         NaN
1267236  tt0169102   NaN         NaN
1267237  tt0169102   NaN         NaN
1267238  tt0169102   NaN         NaN
1267239  tt0169102   NaN         NaN
1267240  tt0169102   NaN         NaN
1267241  tt0169102   NaN         NaN
1267242  tt0169102   NaN         NaN
1267243  tt0169102   NaN         NaN
1267244  tt0169102   NaN         NaN
1267245  tt0169102   NaN         NaN
1267246  tt0169102   NaN         NaN
1267247  tt0169102   NaN         NaN
1267248  tt0169102   NaN         NaN
1267249  tt0169102   NaN         NaN

[1267250 rows x 3 columns]

In [24]:
result.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1267250 entries, 0 to 1267249
Data columns (total 3 columns):
MID     1267250 non-null object
STAR    175914 non-null float64
UID     205708 non-null object
dtypes: float64(1), object(2)
memory usage: 29.0+ MB


In [25]:
# To delete NAN in UID column
result = result[result['UID'].isnull() == False]
result

MID  STAR         UID
0        tt0111161  10.0   ur2509775
1        tt0111161  10.0   ur0997166
2        tt0111161   NaN   ur1005460
3        tt0111161  10.0   ur1898687
4        tt0111161   NaN   ur0094239
5        tt0111161   8.0   ur1285640
6        tt0111161  10.0   ur0611718
7        tt0111161  10.0   ur0257957
8        tt0111161  10.0   ur0355122
9        tt0111161  10.0   ur0842118
10       tt0111161  10.0  ur16117882
11       tt0111161  10.0   ur0174908
12       tt0111161  10.0   ur0265899
13       tt0111161  10.0  ur16161013
14       tt0111161   8.0   ur0226855
15       tt0111161  10.0   ur1003471
16       tt0111161  10.0   ur9365949
17       tt0111161  10.0  ur20345143
18       tt0111161  10.0   ur0043337
19       tt0111161   8.0   ur1532177
20       tt0111161  10.0  ur24573739
21       tt0111161  10.0   ur9871443
22       tt0111161   7.0   ur6657969
23       tt0111161  10.0  ur31182745
24       tt0111161  10.0  ur29409681
25       tt0111161   7.0   ur0138488
26       tt0111161  10.0   ur8635707
27       tt0111161   NaN   ur0082617
28       tt0111161  10.0  ur17447627
29       tt0111161   NaN   ur0643062
...            ...   ...         ...
1262399  tt0169102   NaN   ur2498434
1262400  tt0169102   NaN   ur1527854
1262401  tt0169102  10.0   ur1119267
1262402  tt0169102   4.0  ur15478585
1262403  tt0169102   8.0  ur10948088
1262404  tt0169102   7.0   ur4540074
1262405  tt0169102   NaN   ur3518481
1262406  tt0169102   NaN   ur0574035
1262407  tt0169102   7.0   ur0912441
1262408  tt0169102   1.0  ur12924719
1262409  tt0169102   7.0  ur34567012
1262410  tt0169102   6.0  ur10587962
1262411  tt0169102   NaN   ur2366009
1262412  tt0169102   4.0   ur0527288
1262413  tt0169102   6.0   ur0391152
1262414  tt0169102   3.0   ur0455012
1262415  tt0169102   1.0   ur3600973
1262416  tt0169102   4.0   ur1600076
1262417  tt0169102   1.0   ur1228653
1262418  tt0169102   5.0   ur3522562
1262419  tt0169102   3.0   ur0305537
1262420  tt0169102   2.0   ur1684817
1262421  tt0169102   2.0   ur1928278
1262422  tt0169102   2.0   ur0541597
1262423  tt0169102   1.0   ur1351778
1262424  tt0169102   3.0   ur0239428
1262425  tt0169102   1.0   ur0945264
1262426  tt0169102   1.0   ur1557088
1262427  tt0169102   1.0   ur2081542
1262428  tt0169102   1.0   ur1251318

[205708 rows x 3 columns]

In [26]:
# Fill NAN with mean in each group

MID_STAR_UID = result.groupby('MID').transform(lambda x: x.fillna(x.mean()))

In [27]:
# Add MID column back and change 'STAR' 'UID' type
MID_STAR_UID = pd.concat([MID_STAR_UID,result[['MID']]], axis = 1)
MID_STAR_UID['STAR'] = MID_STAR_UID['STAR'].astype(int)
#MID_STAR_UID['UID'] = MID_STAR_UID['UID'].astype(int)
MID_STAR_UID

STAR        MID
0          10  tt0111161
1          10  tt0111161
2           9  tt0111161
3          10  tt0111161
4           9  tt0111161
5           8  tt0111161
6          10  tt0111161
7          10  tt0111161
8          10  tt0111161
9          10  tt0111161
10         10  tt0111161
11         10  tt0111161
12         10  tt0111161
13         10  tt0111161
14          8  tt0111161
15         10  tt0111161
16         10  tt0111161
17         10  tt0111161
18         10  tt0111161
19          8  tt0111161
20         10  tt0111161
21         10  tt0111161
22          7  tt0111161
23         10  tt0111161
24         10  tt0111161
25          7  tt0111161
26         10  tt0111161
27          9  tt0111161
28         10  tt0111161
29          9  tt0111161
...       ...        ...
1262399     8  tt0169102
1262400     8  tt0169102
1262401    10  tt0169102
1262402     4  tt0169102
1262403     8  tt0169102
1262404     7  tt0169102
1262405     8  tt0169102
1262406     8  tt0169102
1262407     7  tt0169102
1262408     1  tt0169102
1262409     7  tt0169102
1262410     6  tt0169102
1262411     8  tt0169102
1262412     4  tt0169102
1262413     6  tt0169102
1262414     3  tt0169102
1262415     1  tt0169102
1262416     4  tt0169102
1262417     1  tt0169102
1262418     5  tt0169102
1262419     3  tt0169102
1262420     2  tt0169102
1262421     2  tt0169102
1262422     2  tt0169102
1262423     1  tt0169102
1262424     3  tt0169102
1262425     1  tt0169102
1262426     1  tt0169102
1262427     1  tt0169102
1262428     1  tt0169102

[205708 rows x 2 columns]

In [32]:
MID_STAR_UID = pd.concat([MID_STAR_UID,result[["UID"]]], axis = 1)
MID_STAR_UID

STAR         UID        MID
0          10   ur2509775  tt0111161
1          10   ur0997166  tt0111161
2           9   ur1005460  tt0111161
3          10   ur1898687  tt0111161
4           9   ur0094239  tt0111161
5           8   ur1285640  tt0111161
6          10   ur0611718  tt0111161
7          10   ur0257957  tt0111161
8          10   ur0355122  tt0111161
9          10   ur0842118  tt0111161
10         10  ur16117882  tt0111161
11         10   ur0174908  tt0111161
12         10   ur0265899  tt0111161
13         10  ur16161013  tt0111161
14          8   ur0226855  tt0111161
15         10   ur1003471  tt0111161
16         10   ur9365949  tt0111161
17         10  ur20345143  tt0111161
18         10   ur0043337  tt0111161
19          8   ur1532177  tt0111161
20         10  ur24573739  tt0111161
21         10   ur9871443  tt0111161
22          7   ur6657969  tt0111161
23         10  ur31182745  tt0111161
24         10  ur29409681  tt0111161
25          7   ur0138488  tt0111161
26         10   ur8635707  tt0111161
27          9   ur0082617  tt0111161
28         10  ur17447627  tt0111161
29          9   ur0643062  tt0111161
...       ...         ...        ...
1262399     8   ur2498434  tt0169102
1262400     8   ur1527854  tt0169102
1262401    10   ur1119267  tt0169102
1262402     4  ur15478585  tt0169102
1262403     8  ur10948088  tt0169102
1262404     7   ur4540074  tt0169102
1262405     8   ur3518481  tt0169102
1262406     8   ur0574035  tt0169102
1262407     7   ur0912441  tt0169102
1262408     1  ur12924719  tt0169102
1262409     7  ur34567012  tt0169102
1262410     6  ur10587962  tt0169102
1262411     8   ur2366009  tt0169102
1262412     4   ur0527288  tt0169102
1262413     6   ur0391152  tt0169102
1262414     3   ur0455012  tt0169102
1262415     1   ur3600973  tt0169102
1262416     4   ur1600076  tt0169102
1262417     1   ur1228653  tt0169102
1262418     5   ur3522562  tt0169102
1262419     3   ur0305537  tt0169102
1262420     2   ur1684817  tt0169102
1262421     2   ur1928278  tt0169102
1262422     2   ur0541597  tt0169102
1262423     1   ur1351778  tt0169102
1262424     3   ur0239428  tt0169102
1262425     1   ur0945264  tt0169102
1262426     1   ur1557088  tt0169102
1262427     1   ur2081542  tt0169102
1262428     1   ur1251318  tt0169102

[205708 rows x 3 columns]

In [33]:
MID_STAR_UID.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 205708 entries, 0 to 1262428
Data columns (total 3 columns):
STAR    205708 non-null int64
UID     205708 non-null object
MID     205708 non-null object
dtypes: int64(1), object(2)
memory usage: 6.3+ MB


In [34]:
pivot = MID_STAR_UID.pivot_table(values='STAR',index='UID',columns='MID')
pivot

MID        tt0012349  tt0015864  tt0017136  tt0017925  tt0018455  tt0019254  \
UID                                                                           
ur0000006        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000011        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000037        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000039        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000059        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000066        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000075        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000138        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000157        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000229        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000301        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000554        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000578        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000595        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000602        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000685        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000917        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001071        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001107        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001165        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001220        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001246        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001379        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001529        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001586        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001593        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001713        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001757        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001785        NaN        NaN        NaN        NaN        NaN        NaN   
ur0002216        NaN        NaN        NaN        NaN        NaN        NaN   
...              ...        ...        ...        ...        ...        ...   
ur9987422        NaN        NaN        NaN        NaN        NaN        NaN   
ur9987780        NaN        NaN        NaN        NaN        NaN        NaN   
ur9987799        9.0       10.0        NaN       10.0       10.0        NaN   
ur9988421        NaN        NaN        NaN        NaN        NaN        NaN   
ur9988550        NaN        NaN        NaN        NaN        NaN        NaN   
ur9988767        NaN        NaN        NaN        NaN        NaN        NaN   
ur9989450        NaN        NaN        NaN        NaN        NaN        NaN   
ur9989888        NaN        NaN        NaN        NaN        NaN        NaN   
ur9990132        NaN        NaN        NaN        NaN        NaN        NaN   
ur9990302        NaN        NaN        NaN        NaN        NaN        NaN   
ur9990393        NaN        NaN        NaN        NaN        NaN        NaN   
ur9990913        NaN        NaN        NaN        NaN        NaN        NaN   
ur9991099        NaN        NaN        NaN        NaN        NaN        NaN   
ur9991515        NaN        NaN        NaN        NaN        NaN        NaN   
ur9991588        NaN        NaN        NaN        NaN        NaN        NaN   
ur9992507        NaN        NaN        NaN        NaN        NaN        NaN   
ur9992743        NaN        NaN        NaN        NaN        NaN        NaN   
ur9993270        NaN        NaN        NaN        

In [37]:
print "Number of reviews: " + str(len(MID_STAR_UID))
print "Number of users: " + str(pivot.index.shape[0])
print "Number of movies: " + str(len(pivot.columns))

Number of reviews: 205708
Number of users: 111006
Number of movies: 250


In [38]:
MID_STAR_UID.to_csv('MID_STAR_UID.csv')

In [39]:
pivot.to_csv('pivot.csv')

### Dataset Extension

In [268]:
import pickle
with open('../../../Extra_movies/uid','rb') as f:
    uid_ext = pickle.load(f)

In [269]:
uid_ext

tt0120915 tt0121765 tt0185937 tt0121766 tt0499549 tt2975590 tt0335345  \
0      0556667   0343585   0488231   1551736  22532965  27874480   2696560   
1      1383008   1118579   0457497   2106076  22516874  22015342   3756727   
2      0390526   4989916   0517315   1455442  13407466  39517558   3749117   
3      0227441   1318499   0359029   2228260   2064686   2384558   2231676   
4      0454136   3098736   0391725   1713274   2898980  25591817   3824745   
5      0112237  35359466   0772296   2626394  22561863  65932185   0176092   
6      0035229   1042656   0408492   3234629   5378817  36291002   1699441   
7      2175562   1941835   0172836   4514304  16237357  30151001   3192976   
8     11701403   5528333   0714093   5348410  19511193  65936446   0355122   
9     15216305  23465100  19981632   3718653  17767193  13993997   1874588   
10    27714720   1905475   4598948   0762960  20287260  66014594   4445210   
11     4542533   2488512   1492434   1440032   9034138  30464737  15040581   
12    10215382  29348863   2125103   4569419  18853862  66016636   3092424   
13    35359466   0375636   0415125   5277640  22655468  18267388   1758629   
14     9634321  48573956   0794339   0976782  14984420  14032848  11013064   
15    23973392   0901871   0073221   3724887  11558751  66507729   1355507   
16     1301124   1481985   0206062   4445210  10656343   6875736  13044422   
17     1188746  35429467   0445891   3487897  17546726  44372732   1597683   
18     0095638  50687521   0166571   5340143  10427060   3925693   2471566   
19     0990849  59091277   0839523   4417822   1903880  45091733   3230040   
20    25299734  24362496   0187170   5335621  20724086  65198002   4915902   
21    11711870  53645293  11507412   0830088  17571847  59219310   4027777   
22     0216513  20256336   1845052   3524638   3278830  66069699   9185690   
23     0062104   1751658   0679376   4254034   0791177   2637494   2495575   
24    19988908   0625296   0927117   1520422   0856519  64736770  12652007   
25    64599094  59775972   2719706   1556343   8200618   0367663   0643062   
26    64611104  10115534   0132794   5502394  22671754  37599117   4246001   
27     0412272   4597795  19533154   2566393  23495323  60195330   1532177   
28    20552756   1748636   0455869   4194605  10583368  66667854   3927977   
29     0731006   0125528  23708517   5346547  22535510  51791729  60031202   
...        ...       ...       ...       ...       ...       ...       ...   
7839      None      None      None      None      None      None      None   
7840      None      None      None      None      None      None      None   
7841      None      None      None      None      None      None      None   
7842      None      None      None      None      None      None      None   
7843      None      None      None      None      None      None      None   
7844      None      None      None      None      None      None      None   
7845      None      None      None      None      None      None      None   
7846      None      None      None      None      None      None      None   
7847      None      None      None      None      None      None      None   
7848      None      None      None      None      None      None      None   
7849      None      None      None      None      None      None      None   
7850      None      None      None      None      None      None      None   
7851      None      None      None      None      None      None      None   
7852      None      None      None      None      None      None      None   
7853      None      None      None      None      None      None      None   
7854      None      None      None      None      None      None      None   
7855      None      None      None      None      None      None      None   
7856      None      None      None      None      None      None      None   
7857      None      None      None      None      None      None      None   
7858      None      None   

In [277]:
uid_ext = uid_ext.T.groupby(level=0).first().T

In [290]:
import pickle
with open('../../../Extra_movies/star','rb') as f:
    star_ext = pickle.load(f)

In [293]:
star_ext = star_ext.T.groupby(level=0).first().T

In [297]:
star_ext.to_csv('star_ext.csv')

In [304]:
import pickle
with open('../../../Extra_movies/reviews','rb') as f:
    reviews_ext = pickle.load(f)

In [305]:
reviews_ext =reviews_ext.T.groupby(level=0).first().T

In [307]:
reviews_ext.to_csv('reviews_ext.csv',encoding='utf-8')

In [315]:
uid_ext

tt0070047   tt0072271   tt0077651   tt0096895   tt0116629   tt0117571  \
0      2286500.0    228892.0    355122.0    562732.0    166205.0   1293485.0   
1      1298472.0   1328109.0   2698183.0   1293485.0   4491531.0   1125206.0   
2       176175.0   1928674.0     78506.0   5044573.0    438881.0    691174.0   
3       660441.0   2176149.0   3286216.0   2402868.0   1111192.0      7719.0   
4      1293485.0    381265.0   3942316.0    915482.0  17646017.0   1002035.0   
5      4216884.0   2755840.0    195342.0   3924830.0   5183897.0   3756685.0   
6      1377414.0   1293485.0   1293485.0    102816.0  17406951.0    111563.0   
7      6880633.0   1661526.0   5031035.0   2565039.0    461729.0   3103298.0   
8     19658928.0   2436813.0   4550926.0   1002035.0   8282981.0   8737514.0   
9       375889.0   2789183.0   1601212.0   4248714.0   1211113.0   5156288.0   
10      510950.0  17699578.0   2286081.0   4614141.0   2156865.0  23747219.0   
11     8987710.0   2284989.0  21887825.0   2149970.0  24419014.0   3174947.0   
12     3270789.0  19981632.0  15311310.0  21218938.0   2018105.0   2890802.0   
13    14150505.0    812757.0   5483548.0   6363971.0  10266223.0  29937976.0   
14     3174947.0   4055726.0  22528459.0  21028881.0  11358844.0  17571044.0   
15      355122.0    643062.0  28251377.0  21135959.0    774002.0   2236837.0   
16     4234119.0    556157.0   9104237.0   3454750.0   4991047.0    892646.0   
17      547823.0  13414573.0  16328348.0   4425690.0   1024222.0   5876717.0   
18      643062.0  36262902.0  56761070.0  40565212.0    142781.0  25364506.0   
19      109433.0  33359914.0  63109920.0  20753524.0  15327206.0    622275.0   
20     4445210.0    157517.0  12421091.0  32227901.0    102706.0  26200236.0   
21    27690706.0   3270789.0   4145056.0  23059956.0   1107635.0  21320033.0   
22     2707735.0   4974986.0  63098806.0  20150650.0  61453893.0   6981752.0   
23      892646.0   4095958.0   9725326.0   5808358.0    309353.0  30299837.0   
24     3377070.0   4407113.0  20018357.0   7611232.0   1705076.0   1327543.0   
25      650255.0   9202258.0  24826223.0    779095.0   1238706.0   6918917.0   
26     6643268.0   3840686.0  26660679.0  33328657.0   1532177.0  21231800.0   
27    22772275.0   2651286.0   8566077.0  32939276.0    294077.0  26281817.0   
28    19892172.0   2396823.0   6328647.0  15209258.0  15148330.0  26336627.0   
29    21885947.0  36357573.0   7752337.0  16832848.0    940840.0  25268903.0   
...          ...         ...         ...         ...         ...         ...   
7839         NaN         NaN         NaN         NaN         NaN         NaN   
7840         NaN         NaN         NaN         NaN         NaN         NaN   
7841         NaN         NaN         NaN         NaN         NaN         NaN   
7842         NaN         NaN         NaN         NaN         NaN         NaN   
7843         NaN         NaN         NaN         NaN         NaN         NaN   
7844         NaN         NaN         NaN         NaN         NaN         NaN   
7845         NaN         NaN         NaN         NaN         NaN         NaN   
7846         NaN         NaN         NaN         NaN         NaN         NaN   
7847         NaN         NaN         NaN         NaN         NaN         NaN   
7848         NaN         NaN         NaN         NaN         NaN         NaN   
7849         NaN         NaN         NaN         NaN         NaN         NaN   
7850         NaN         NaN         NaN         NaN         NaN         NaN   
7851         NaN         NaN         NaN         NaN         NaN         NaN   
7852         NaN         NaN         NaN         NaN         NaN         NaN   
7853         NaN         NaN         NaN         NaN         NaN         NaN   
7854         NaN         NaN         NaN         NaN         NaN         NaN   
7855         NaN         NaN         NaN         NaN         NaN         NaN   
7856         NaN         NaN         NaN         NaN         NaN         NaN   
7857   

In [320]:
'ur'+str(int(uid_ext['tt0070047'][0]))

'ur2286500'

In [331]:
np.isnan(uid_ext['tt0070047'][3])

False

In [333]:
def fff(x):
    if np.isnan(x) == False:
        return 'ur'+ str(int(x))
uid_ext = uid_ext.applymap(fff)

In [334]:
uid_ext

tt0070047   tt0072271   tt0077651   tt0096895   tt0116629   tt0117571  \
0      ur2286500    ur228892    ur355122    ur562732    ur166205   ur1293485   
1      ur1298472   ur1328109   ur2698183   ur1293485   ur4491531   ur1125206   
2       ur176175   ur1928674     ur78506   ur5044573    ur438881    ur691174   
3       ur660441   ur2176149   ur3286216   ur2402868   ur1111192      ur7719   
4      ur1293485    ur381265   ur3942316    ur915482  ur17646017   ur1002035   
5      ur4216884   ur2755840    ur195342   ur3924830   ur5183897   ur3756685   
6      ur1377414   ur1293485   ur1293485    ur102816  ur17406951    ur111563   
7      ur6880633   ur1661526   ur5031035   ur2565039    ur461729   ur3103298   
8     ur19658928   ur2436813   ur4550926   ur1002035   ur8282981   ur8737514   
9       ur375889   ur2789183   ur1601212   ur4248714   ur1211113   ur5156288   
10      ur510950  ur17699578   ur2286081   ur4614141   ur2156865  ur23747219   
11     ur8987710   ur2284989  ur21887825   ur2149970  ur24419014   ur3174947   
12     ur3270789  ur19981632  ur15311310  ur21218938   ur2018105   ur2890802   
13    ur14150505    ur812757   ur5483548   ur6363971  ur10266223  ur29937976   
14     ur3174947   ur4055726  ur22528459  ur21028881  ur11358844  ur17571044   
15      ur355122    ur643062  ur28251377  ur21135959    ur774002   ur2236837   
16     ur4234119    ur556157   ur9104237   ur3454750   ur4991047    ur892646   
17      ur547823  ur13414573  ur16328348   ur4425690   ur1024222   ur5876717   
18      ur643062  ur36262902  ur56761070  ur40565212    ur142781  ur25364506   
19      ur109433  ur33359914  ur63109920  ur20753524  ur15327206    ur622275   
20     ur4445210    ur157517  ur12421091  ur32227901    ur102706  ur26200236   
21    ur27690706   ur3270789   ur4145056  ur23059956   ur1107635  ur21320033   
22     ur2707735   ur4974986  ur63098806  ur20150650  ur61453893   ur6981752   
23      ur892646   ur4095958   ur9725326   ur5808358    ur309353  ur30299837   
24     ur3377070   ur4407113  ur20018357   ur7611232   ur1705076   ur1327543   
25      ur650255   ur9202258  ur24826223    ur779095   ur1238706   ur6918917   
26     ur6643268   ur3840686  ur26660679  ur33328657   ur1532177  ur21231800   
27    ur22772275   ur2651286   ur8566077  ur32939276    ur294077  ur26281817   
28    ur19892172   ur2396823   ur6328647  ur15209258  ur15148330  ur26336627   
29    ur21885947  ur36357573   ur7752337  ur16832848    ur940840  ur25268903   
...          ...         ...         ...         ...         ...         ...   
7839        None        None        None        None        None        None   
7840        None        None        None        None        None        None   
7841        None        None        None        None        None        None   
7842        None        None        None        None        None        None   
7843        None        None        None        None        None        None   
7844        None        None        None        None        None        None   
7845        None        None        None        None        None        None   
7846        None        None        None        None        None        None   
7847        None        None        None        None        None        None   
7848        None        None        None        None        None        None   
7849        None        None        None        None        None        None   
7850        None        None        None        None        None        None   
7851        None        None        None        None        None        None   
7852        None        None        None        None        None        None   
7853        None        None        None        None        None        None   
7854        None        None        None        None        None        None   
7855        None        None        None        None        None        None   
7856        None        None        None        None        None        None   
7857   

In [335]:
uid_ext.to_csv('uid_ext.csv')

In [336]:
uid_ext = pd.read_csv('uid_ext.csv')

In [338]:
del uid_ext['Unnamed: 0']

In [344]:
id_list_ext = uid_ext.columns.values


In [345]:
# To create MID_UID dataframe
complex_table = pd.DataFrame(columns = ['MID','UID'])
tables = []
for i in id_list_ext:
    table = pd.melt(uid_ext,value_vars=[i],var_name = 'MID', value_name = 'UID')
    tables.append(table)
MID_UID_EXT = complex_table.append(tables,ignore_index=True)

In [346]:
MID_UID_EXT

MID         UID
0        tt0070047   ur2286500
1        tt0070047   ur1298472
2        tt0070047    ur176175
3        tt0070047    ur660441
4        tt0070047   ur1293485
5        tt0070047   ur4216884
6        tt0070047   ur1377414
7        tt0070047   ur6880633
8        tt0070047  ur19658928
9        tt0070047    ur375889
10       tt0070047    ur510950
11       tt0070047   ur8987710
12       tt0070047   ur3270789
13       tt0070047  ur14150505
14       tt0070047   ur3174947
15       tt0070047    ur355122
16       tt0070047   ur4234119
17       tt0070047    ur547823
18       tt0070047    ur643062
19       tt0070047    ur109433
20       tt0070047   ur4445210
21       tt0070047  ur27690706
22       tt0070047   ur2707735
23       tt0070047    ur892646
24       tt0070047   ur3377070
25       tt0070047    ur650255
26       tt0070047   ur6643268
27       tt0070047  ur22772275
28       tt0070047  ur19892172
29       tt0070047  ur21885947
...            ...         ...
1817709  tt3498820         NaN
1817710  tt3498820         NaN
1817711  tt3498820         NaN
1817712  tt3498820         NaN
1817713  tt3498820         NaN
1817714  tt3498820         NaN
1817715  tt3498820         NaN
1817716  tt3498820         NaN
1817717  tt3498820         NaN
1817718  tt3498820         NaN
1817719  tt3498820         NaN
1817720  tt3498820         NaN
1817721  tt3498820         NaN
1817722  tt3498820         NaN
1817723  tt3498820         NaN
1817724  tt3498820         NaN
1817725  tt3498820         NaN
1817726  tt3498820         NaN
1817727  tt3498820         NaN
1817728  tt3498820         NaN
1817729  tt3498820         NaN
1817730  tt3498820         NaN
1817731  tt3498820         NaN
1817732  tt3498820         NaN
1817733  tt3498820         NaN
1817734  tt3498820         NaN
1817735  tt3498820         NaN
1817736  tt3498820         NaN
1817737  tt3498820         NaN
1817738  tt3498820         NaN

[1817739 rows x 2 columns]

In [347]:
len(MID_UID_EXT['UID'].unique())

169502

In [348]:
star_ext = pd.read_csv('star_ext.csv')

In [349]:
del star_ext['Unnamed: 0']

In [350]:
star_ext

tt0070047  tt0072271  tt0077651  tt0096895  tt0116629  tt0117571  \
0          10.0       10.0       10.0       10.0        NaN       10.0   
1           NaN        9.0       10.0       10.0        7.0        8.0   
2          10.0       10.0        NaN       10.0       10.0        NaN   
3          10.0       10.0        9.0        8.0        8.0       10.0   
4          10.0        NaN       10.0        7.0       10.0        NaN   
5          10.0       10.0        NaN        9.0        1.0       10.0   
6           NaN       10.0       10.0        8.0        8.0        9.0   
7          10.0       10.0       10.0        8.0       10.0        8.0   
8           9.0       10.0        NaN        NaN        7.0       10.0   
9          10.0       10.0       10.0       10.0        1.0        8.0   
10          7.0       10.0       10.0        9.0        1.0       10.0   
11          8.0        NaN        1.0        2.0        1.0        8.0   
12          8.0        9.0       10.0       10.0        1.0       10.0   
13         10.0       10.0       10.0       10.0        8.0        8.0   
14          8.0       10.0        1.0       10.0        8.0        9.0   
15          6.0        NaN       10.0       10.0        1.0        1.0   
16         10.0       10.0       10.0       10.0        1.0       10.0   
17          9.0       10.0       10.0       10.0        1.0        8.0   
18          NaN        1.0       10.0       10.0        1.0       10.0   
19          1.0        1.0       10.0        NaN        1.0        8.0   
20          9.0       10.0       10.0       10.0        1.0       10.0   
21         10.0        7.0       10.0        NaN        1.0       10.0   
22         10.0        9.0        9.0        9.0        8.0        7.0   
23         10.0       10.0        8.0       10.0       10.0        8.0   
24         10.0       10.0        NaN       10.0        1.0        7.0   
25          6.0        9.0        1.0       10.0        1.0        7.0   
26          9.0        NaN        8.0       10.0        7.0        8.0   
27          5.0       10.0       10.0       10.0        1.0        8.0   
28          9.0       10.0       10.0       10.0        4.0        9.0   
29          NaN        4.0       10.0       10.0        8.0       10.0   
...         ...        ...        ...        ...        ...        ...   
7839        NaN        NaN        NaN        NaN        NaN        NaN   
7840        NaN        NaN        NaN        NaN        NaN        NaN   
7841        NaN        NaN        NaN        NaN        NaN        NaN   
7842        NaN        NaN        NaN        NaN        NaN        NaN   
7843        NaN        NaN        NaN        NaN        NaN        NaN   
7844        NaN        NaN        NaN        NaN        NaN        NaN   
7845        NaN        NaN        NaN        NaN        NaN        NaN   
7846        NaN        NaN        NaN        NaN        NaN        NaN   
7847        NaN        NaN        NaN        NaN        NaN        NaN   
7848        NaN        NaN        NaN        NaN        NaN        NaN   
7849        NaN        NaN        NaN        NaN        NaN        NaN   
7850        NaN        NaN        NaN        NaN        NaN        NaN   
7851        NaN        NaN        NaN        NaN        NaN        NaN   
7852        NaN        NaN        NaN        NaN        NaN        NaN   
7853        NaN        NaN        NaN        NaN        NaN        NaN   
7854        NaN        NaN        NaN        NaN        NaN        NaN   
7855        NaN        NaN        NaN        NaN        NaN        NaN   
7856        NaN        NaN        NaN        NaN        NaN        NaN   
7857        NaN        NaN        NaN        NaN        NaN        NaN   
7858        NaN        NaN        NaN        NaN        NaN        NaN   
7859        NaN        NaN        NaN        NaN        NaN        NaN   
7860        NaN        NaN        NaN        NaN        NaN        NaN   
7861      

In [351]:
# To create MID_STAR dataframe
complex_table = pd.DataFrame(columns = ['MID','STAR'])
tables = []
for i in id_list_ext:
    table = pd.melt(star_ext,value_vars=[i],var_name = 'MID', value_name = 'STAR')
    tables.append(table)
MID_STAR_EXT = complex_table.append(tables,ignore_index=True)

In [352]:
MID_STAR_EXT

MID  STAR
0        tt0070047  10.0
1        tt0070047   NaN
2        tt0070047  10.0
3        tt0070047  10.0
4        tt0070047  10.0
5        tt0070047  10.0
6        tt0070047   NaN
7        tt0070047  10.0
8        tt0070047   9.0
9        tt0070047  10.0
10       tt0070047   7.0
11       tt0070047   8.0
12       tt0070047   8.0
13       tt0070047  10.0
14       tt0070047   8.0
15       tt0070047   6.0
16       tt0070047  10.0
17       tt0070047   9.0
18       tt0070047   NaN
19       tt0070047   1.0
20       tt0070047   9.0
21       tt0070047  10.0
22       tt0070047  10.0
23       tt0070047  10.0
24       tt0070047  10.0
25       tt0070047   6.0
26       tt0070047   9.0
27       tt0070047   5.0
28       tt0070047   9.0
29       tt0070047   NaN
...            ...   ...
1817709  tt3498820   NaN
1817710  tt3498820   NaN
1817711  tt3498820   NaN
1817712  tt3498820   NaN
1817713  tt3498820   NaN
1817714  tt3498820   NaN
1817715  tt3498820   NaN
1817716  tt3498820   NaN
1817717  tt3498820   NaN
1817718  tt3498820   NaN
1817719  tt3498820   NaN
1817720  tt3498820   NaN
1817721  tt3498820   NaN
1817722  tt3498820   NaN
1817723  tt3498820   NaN
1817724  tt3498820   NaN
1817725  tt3498820   NaN
1817726  tt3498820   NaN
1817727  tt3498820   NaN
1817728  tt3498820   NaN
1817729  tt3498820   NaN
1817730  tt3498820   NaN
1817731  tt3498820   NaN
1817732  tt3498820   NaN
1817733  tt3498820   NaN
1817734  tt3498820   NaN
1817735  tt3498820   NaN
1817736  tt3498820   NaN
1817737  tt3498820   NaN
1817738  tt3498820   NaN

[1817739 rows x 2 columns]

In [353]:
# To create MID_STAR_UID dataframe
result = pd.concat([MID_STAR_EXT,MID_UID_EXT],axis=1,ignore_index=True)
result.columns = ['MID','STAR','MID2','UID']
result.drop('MID2',axis=1,inplace=True)
result

MID  STAR         UID
0        tt0070047  10.0   ur2286500
1        tt0070047   NaN   ur1298472
2        tt0070047  10.0    ur176175
3        tt0070047  10.0    ur660441
4        tt0070047  10.0   ur1293485
5        tt0070047  10.0   ur4216884
6        tt0070047   NaN   ur1377414
7        tt0070047  10.0   ur6880633
8        tt0070047   9.0  ur19658928
9        tt0070047  10.0    ur375889
10       tt0070047   7.0    ur510950
11       tt0070047   8.0   ur8987710
12       tt0070047   8.0   ur3270789
13       tt0070047  10.0  ur14150505
14       tt0070047   8.0   ur3174947
15       tt0070047   6.0    ur355122
16       tt0070047  10.0   ur4234119
17       tt0070047   9.0    ur547823
18       tt0070047   NaN    ur643062
19       tt0070047   1.0    ur109433
20       tt0070047   9.0   ur4445210
21       tt0070047  10.0  ur27690706
22       tt0070047  10.0   ur2707735
23       tt0070047  10.0    ur892646
24       tt0070047  10.0   ur3377070
25       tt0070047   6.0    ur650255
26       tt0070047   9.0   ur6643268
27       tt0070047   5.0  ur22772275
28       tt0070047   9.0  ur19892172
29       tt0070047   NaN  ur21885947
...            ...   ...         ...
1817709  tt3498820   NaN         NaN
1817710  tt3498820   NaN         NaN
1817711  tt3498820   NaN         NaN
1817712  tt3498820   NaN         NaN
1817713  tt3498820   NaN         NaN
1817714  tt3498820   NaN         NaN
1817715  tt3498820   NaN         NaN
1817716  tt3498820   NaN         NaN
1817717  tt3498820   NaN         NaN
1817718  tt3498820   NaN         NaN
1817719  tt3498820   NaN         NaN
1817720  tt3498820   NaN         NaN
1817721  tt3498820   NaN         NaN
1817722  tt3498820   NaN         NaN
1817723  tt3498820   NaN         NaN
1817724  tt3498820   NaN         NaN
1817725  tt3498820   NaN         NaN
1817726  tt3498820   NaN         NaN
1817727  tt3498820   NaN         NaN
1817728  tt3498820   NaN         NaN
1817729  tt3498820   NaN         NaN
1817730  tt3498820   NaN         NaN
1817731  tt3498820   NaN         NaN
1817732  tt3498820   NaN         NaN
1817733  tt3498820   NaN         NaN
1817734  tt3498820   NaN         NaN
1817735  tt3498820   NaN         NaN
1817736  tt3498820   NaN         NaN
1817737  tt3498820   NaN         NaN
1817738  tt3498820   NaN         NaN

[1817739 rows x 3 columns]

In [196]:
result.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1967250 entries, 0 to 1967249
Data columns (total 3 columns):
MID     object
STAR    float64
UID     object
dtypes: float64(1), object(2)
memory usage: 45.0+ MB


In [354]:
# To delete NAN in UID column
result = result[result['UID'].isnull() == False]
result

MID  STAR         UID
0        tt0070047  10.0   ur2286500
1        tt0070047   NaN   ur1298472
2        tt0070047  10.0    ur176175
3        tt0070047  10.0    ur660441
4        tt0070047  10.0   ur1293485
5        tt0070047  10.0   ur4216884
6        tt0070047   NaN   ur1377414
7        tt0070047  10.0   ur6880633
8        tt0070047   9.0  ur19658928
9        tt0070047  10.0    ur375889
10       tt0070047   7.0    ur510950
11       tt0070047   8.0   ur8987710
12       tt0070047   8.0   ur3270789
13       tt0070047  10.0  ur14150505
14       tt0070047   8.0   ur3174947
15       tt0070047   6.0    ur355122
16       tt0070047  10.0   ur4234119
17       tt0070047   9.0    ur547823
18       tt0070047   NaN    ur643062
19       tt0070047   1.0    ur109433
20       tt0070047   9.0   ur4445210
21       tt0070047  10.0  ur27690706
22       tt0070047  10.0   ur2707735
23       tt0070047  10.0    ur892646
24       tt0070047  10.0   ur3377070
25       tt0070047   6.0    ur650255
26       tt0070047   9.0   ur6643268
27       tt0070047   5.0  ur22772275
28       tt0070047   9.0  ur19892172
29       tt0070047   NaN  ur21885947
...            ...   ...         ...
1810950  tt3498820   7.0  ur44261895
1810951  tt3498820   8.0  ur66155439
1810952  tt3498820   1.0  ur65968893
1810953  tt3498820  10.0  ur63573225
1810954  tt3498820   8.0   ur6141756
1810955  tt3498820   8.0  ur66508300
1810956  tt3498820   8.0  ur65144894
1810957  tt3498820  10.0  ur54640256
1810958  tt3498820   8.0   ur4535081
1810959  tt3498820   8.0  ur48448272
1810960  tt3498820  10.0  ur61514137
1810961  tt3498820   9.0   ur6136793
1810962  tt3498820   7.0  ur61675071
1810963  tt3498820  10.0  ur65571567
1810964  tt3498820  10.0  ur67378057
1810965  tt3498820  10.0  ur67093391
1810966  tt3498820   7.0  ur47346916
1810967  tt3498820  10.0  ur24337173
1810968  tt3498820   7.0  ur66474046
1810969  tt3498820   5.0  ur65574658
1810970  tt3498820   6.0  ur51120194
1810971  tt3498820  10.0  ur66549718
1810972  tt3498820   4.0  ur18648606
1810973  tt3498820   1.0  ur66654441
1810974  tt3498820   1.0  ur19781397
1810975  tt3498820   1.0  ur47881457
1810976  tt3498820   1.0  ur64382857
1810977  tt3498820   1.0  ur66492584
1810978  tt3498820   1.0  ur65995957
1810979  tt3498820   1.0  ur66024302

[323171 rows x 3 columns]

In [355]:
(result['STAR'].isnull()).value_counts()

False    277042
True      46129
Name: STAR, dtype: int64

In [356]:
result.isnull().any()

MID     False
STAR     True
UID     False
dtype: bool

In [357]:
# Fill NAN with mean in each group

MID_STAR_UID_EXT = result.fillna(result.groupby('MID').transform('mean'))

In [358]:
MID_STAR_UID_EXT

MID       STAR         UID
0        tt0070047  10.000000   ur2286500
1        tt0070047   8.057292   ur1298472
2        tt0070047  10.000000    ur176175
3        tt0070047  10.000000    ur660441
4        tt0070047  10.000000   ur1293485
5        tt0070047  10.000000   ur4216884
6        tt0070047   8.057292   ur1377414
7        tt0070047  10.000000   ur6880633
8        tt0070047   9.000000  ur19658928
9        tt0070047  10.000000    ur375889
10       tt0070047   7.000000    ur510950
11       tt0070047   8.000000   ur8987710
12       tt0070047   8.000000   ur3270789
13       tt0070047  10.000000  ur14150505
14       tt0070047   8.000000   ur3174947
15       tt0070047   6.000000    ur355122
16       tt0070047  10.000000   ur4234119
17       tt0070047   9.000000    ur547823
18       tt0070047   8.057292    ur643062
19       tt0070047   1.000000    ur109433
20       tt0070047   9.000000   ur4445210
21       tt0070047  10.000000  ur27690706
22       tt0070047  10.000000   ur2707735
23       tt0070047  10.000000    ur892646
24       tt0070047  10.000000   ur3377070
25       tt0070047   6.000000    ur650255
26       tt0070047   9.000000   ur6643268
27       tt0070047   5.000000  ur22772275
28       tt0070047   9.000000  ur19892172
29       tt0070047   8.057292  ur21885947
...            ...        ...         ...
1810950  tt3498820   7.000000  ur44261895
1810951  tt3498820   8.000000  ur66155439
1810952  tt3498820   1.000000  ur65968893
1810953  tt3498820  10.000000  ur63573225
1810954  tt3498820   8.000000   ur6141756
1810955  tt3498820   8.000000  ur66508300
1810956  tt3498820   8.000000  ur65144894
1810957  tt3498820  10.000000  ur54640256
1810958  tt3498820   8.000000   ur4535081
1810959  tt3498820   8.000000  ur48448272
1810960  tt3498820  10.000000  ur61514137
1810961  tt3498820   9.000000   ur6136793
1810962  tt3498820   7.000000  ur61675071
1810963  tt3498820  10.000000  ur65571567
1810964  tt3498820  10.000000  ur67378057
1810965  tt3498820  10.000000  ur67093391
1810966  tt3498820   7.000000  ur47346916
1810967  tt3498820  10.000000  ur24337173
1810968  tt3498820   7.000000  ur66474046
1810969  tt3498820   5.000000  ur65574658
1810970  tt3498820   6.000000  ur51120194
1810971  tt3498820  10.000000  ur66549718
1810972  tt3498820   4.000000  ur18648606
1810973  tt3498820   1.000000  ur66654441
1810974  tt3498820   1.000000  ur19781397
1810975  tt3498820   1.000000  ur47881457
1810976  tt3498820   1.000000  ur64382857
1810977  tt3498820   1.000000  ur66492584
1810978  tt3498820   1.000000  ur65995957
1810979  tt3498820   1.000000  ur66024302

[323171 rows x 3 columns]

In [367]:
MID_STAR_UID_EXT['STAR'] = MID_STAR_UID_EXT['STAR'].astype(int)

In [368]:
MID_STAR_UID_EXT

MID  STAR         UID
0        tt0070047    10   ur2286500
1        tt0070047     8   ur1298472
2        tt0070047    10    ur176175
3        tt0070047    10    ur660441
4        tt0070047    10   ur1293485
5        tt0070047    10   ur4216884
6        tt0070047     8   ur1377414
7        tt0070047    10   ur6880633
8        tt0070047     9  ur19658928
9        tt0070047    10    ur375889
10       tt0070047     7    ur510950
11       tt0070047     8   ur8987710
12       tt0070047     8   ur3270789
13       tt0070047    10  ur14150505
14       tt0070047     8   ur3174947
15       tt0070047     6    ur355122
16       tt0070047    10   ur4234119
17       tt0070047     9    ur547823
18       tt0070047     8    ur643062
19       tt0070047     1    ur109433
20       tt0070047     9   ur4445210
21       tt0070047    10  ur27690706
22       tt0070047    10   ur2707735
23       tt0070047    10    ur892646
24       tt0070047    10   ur3377070
25       tt0070047     6    ur650255
26       tt0070047     9   ur6643268
27       tt0070047     5  ur22772275
28       tt0070047     9  ur19892172
29       tt0070047     8  ur21885947
...            ...   ...         ...
1810950  tt3498820     7  ur44261895
1810951  tt3498820     8  ur66155439
1810952  tt3498820     1  ur65968893
1810953  tt3498820    10  ur63573225
1810954  tt3498820     8   ur6141756
1810955  tt3498820     8  ur66508300
1810956  tt3498820     8  ur65144894
1810957  tt3498820    10  ur54640256
1810958  tt3498820     8   ur4535081
1810959  tt3498820     8  ur48448272
1810960  tt3498820    10  ur61514137
1810961  tt3498820     9   ur6136793
1810962  tt3498820     7  ur61675071
1810963  tt3498820    10  ur65571567
1810964  tt3498820    10  ur67378057
1810965  tt3498820    10  ur67093391
1810966  tt3498820     7  ur47346916
1810967  tt3498820    10  ur24337173
1810968  tt3498820     7  ur66474046
1810969  tt3498820     5  ur65574658
1810970  tt3498820     6  ur51120194
1810971  tt3498820    10  ur66549718
1810972  tt3498820     4  ur18648606
1810973  tt3498820     1  ur66654441
1810974  tt3498820     1  ur19781397
1810975  tt3498820     1  ur47881457
1810976  tt3498820     1  ur64382857
1810977  tt3498820     1  ur66492584
1810978  tt3498820     1  ur65995957
1810979  tt3498820     1  ur66024302

[323171 rows x 3 columns]

In [369]:
MID_STAR_UID_EXT.to_csv('MID_STAR_UID_EXT.csv')

In [2]:
MID_STAR_UID_EXT = pd.read_csv('MID_STAR_UID_EXT.csv')

In [4]:
del MID_STAR_UID_EXT['Unnamed: 0']

In [5]:
MID_STAR_UID_EXT

MID  STAR         UID
0       tt0070047    10   ur2286500
1       tt0070047     8   ur1298472
2       tt0070047    10    ur176175
3       tt0070047    10    ur660441
4       tt0070047    10   ur1293485
5       tt0070047    10   ur4216884
6       tt0070047     8   ur1377414
7       tt0070047    10   ur6880633
8       tt0070047     9  ur19658928
9       tt0070047    10    ur375889
10      tt0070047     7    ur510950
11      tt0070047     8   ur8987710
12      tt0070047     8   ur3270789
13      tt0070047    10  ur14150505
14      tt0070047     8   ur3174947
15      tt0070047     6    ur355122
16      tt0070047    10   ur4234119
17      tt0070047     9    ur547823
18      tt0070047     8    ur643062
19      tt0070047     1    ur109433
20      tt0070047     9   ur4445210
21      tt0070047    10  ur27690706
22      tt0070047    10   ur2707735
23      tt0070047    10    ur892646
24      tt0070047    10   ur3377070
25      tt0070047     6    ur650255
26      tt0070047     9   ur6643268
27      tt0070047     5  ur22772275
28      tt0070047     9  ur19892172
29      tt0070047     8  ur21885947
...           ...   ...         ...
323141  tt3498820     7  ur44261895
323142  tt3498820     8  ur66155439
323143  tt3498820     1  ur65968893
323144  tt3498820    10  ur63573225
323145  tt3498820     8   ur6141756
323146  tt3498820     8  ur66508300
323147  tt3498820     8  ur65144894
323148  tt3498820    10  ur54640256
323149  tt3498820     8   ur4535081
323150  tt3498820     8  ur48448272
323151  tt3498820    10  ur61514137
323152  tt3498820     9   ur6136793
323153  tt3498820     7  ur61675071
323154  tt3498820    10  ur65571567
323155  tt3498820    10  ur67378057
323156  tt3498820    10  ur67093391
323157  tt3498820     7  ur47346916
323158  tt3498820    10  ur24337173
323159  tt3498820     7  ur66474046
323160  tt3498820     5  ur65574658
323161  tt3498820     6  ur51120194
323162  tt3498820    10  ur66549718
323163  tt3498820     4  ur18648606
323164  tt3498820     1  ur66654441
323165  tt3498820     1  ur19781397
323166  tt3498820     1  ur47881457
323167  tt3498820     1  ur64382857
323168  tt3498820     1  ur66492584
323169  tt3498820     1  ur65995957
323170  tt3498820     1  ur66024302

[323171 rows x 3 columns]

In [9]:
cols = MID_STAR_UID_EXT.columns.tolist()

In [10]:
cols

['MID', 'STAR', 'UID']

In [11]:
cols = ['MID','UID','STAR']

In [12]:
MID_STAR_UID_EXT = MID_STAR_UID_EXT[cols]

In [13]:
MID_STAR_UID_EXT

MID         UID  STAR
0       tt0070047   ur2286500    10
1       tt0070047   ur1298472     8
2       tt0070047    ur176175    10
3       tt0070047    ur660441    10
4       tt0070047   ur1293485    10
5       tt0070047   ur4216884    10
6       tt0070047   ur1377414     8
7       tt0070047   ur6880633    10
8       tt0070047  ur19658928     9
9       tt0070047    ur375889    10
10      tt0070047    ur510950     7
11      tt0070047   ur8987710     8
12      tt0070047   ur3270789     8
13      tt0070047  ur14150505    10
14      tt0070047   ur3174947     8
15      tt0070047    ur355122     6
16      tt0070047   ur4234119    10
17      tt0070047    ur547823     9
18      tt0070047    ur643062     8
19      tt0070047    ur109433     1
20      tt0070047   ur4445210     9
21      tt0070047  ur27690706    10
22      tt0070047   ur2707735    10
23      tt0070047    ur892646    10
24      tt0070047   ur3377070    10
25      tt0070047    ur650255     6
26      tt0070047   ur6643268     9
27      tt0070047  ur22772275     5
28      tt0070047  ur19892172     9
29      tt0070047  ur21885947     8
...           ...         ...   ...
323141  tt3498820  ur44261895     7
323142  tt3498820  ur66155439     8
323143  tt3498820  ur65968893     1
323144  tt3498820  ur63573225    10
323145  tt3498820   ur6141756     8
323146  tt3498820  ur66508300     8
323147  tt3498820  ur65144894     8
323148  tt3498820  ur54640256    10
323149  tt3498820   ur4535081     8
323150  tt3498820  ur48448272     8
323151  tt3498820  ur61514137    10
323152  tt3498820   ur6136793     9
323153  tt3498820  ur61675071     7
323154  tt3498820  ur65571567    10
323155  tt3498820  ur67378057    10
323156  tt3498820  ur67093391    10
323157  tt3498820  ur47346916     7
323158  tt3498820  ur24337173    10
323159  tt3498820  ur66474046     7
323160  tt3498820  ur65574658     5
323161  tt3498820  ur51120194     6
323162  tt3498820  ur66549718    10
323163  tt3498820  ur18648606     4
323164  tt3498820  ur66654441     1
323165  tt3498820  ur19781397     1
323166  tt3498820  ur47881457     1
323167  tt3498820  ur64382857     1
323168  tt3498820  ur66492584     1
323169  tt3498820  ur65995957     1
323170  tt3498820  ur66024302     1

[323171 rows x 3 columns]

In [14]:
MID_STAR_UID = pd.read_csv('MID_STAR_UID.csv')

In [15]:
del MID_STAR_UID['Unnamed: 0']

In [16]:
MID_STAR_UID

STAR         UID        MID
0         10   ur2509775  tt0111161
1         10   ur0997166  tt0111161
2          9   ur1005460  tt0111161
3         10   ur1898687  tt0111161
4          9   ur0094239  tt0111161
5          8   ur1285640  tt0111161
6         10   ur0611718  tt0111161
7         10   ur0257957  tt0111161
8         10   ur0355122  tt0111161
9         10   ur0842118  tt0111161
10        10  ur16117882  tt0111161
11        10   ur0174908  tt0111161
12        10   ur0265899  tt0111161
13        10  ur16161013  tt0111161
14         8   ur0226855  tt0111161
15        10   ur1003471  tt0111161
16        10   ur9365949  tt0111161
17        10  ur20345143  tt0111161
18        10   ur0043337  tt0111161
19         8   ur1532177  tt0111161
20        10  ur24573739  tt0111161
21        10   ur9871443  tt0111161
22         7   ur6657969  tt0111161
23        10  ur31182745  tt0111161
24        10  ur29409681  tt0111161
25         7   ur0138488  tt0111161
26        10   ur8635707  tt0111161
27         9   ur0082617  tt0111161
28        10  ur17447627  tt0111161
29         9   ur0643062  tt0111161
...      ...         ...        ...
205678     8   ur2498434  tt0169102
205679     8   ur1527854  tt0169102
205680    10   ur1119267  tt0169102
205681     4  ur15478585  tt0169102
205682     8  ur10948088  tt0169102
205683     7   ur4540074  tt0169102
205684     8   ur3518481  tt0169102
205685     8   ur0574035  tt0169102
205686     7   ur0912441  tt0169102
205687     1  ur12924719  tt0169102
205688     7  ur34567012  tt0169102
205689     6  ur10587962  tt0169102
205690     8   ur2366009  tt0169102
205691     4   ur0527288  tt0169102
205692     6   ur0391152  tt0169102
205693     3   ur0455012  tt0169102
205694     1   ur3600973  tt0169102
205695     4   ur1600076  tt0169102
205696     1   ur1228653  tt0169102
205697     5   ur3522562  tt0169102
205698     3   ur0305537  tt0169102
205699     2   ur1684817  tt0169102
205700     2   ur1928278  tt0169102
205701     2   ur0541597  tt0169102
205702     1   ur1351778  tt0169102
205703     3   ur0239428  tt0169102
205704     1   ur0945264  tt0169102
205705     1   ur1557088  tt0169102
205706     1   ur2081542  tt0169102
205707     1   ur1251318  tt0169102

[205708 rows x 3 columns]

In [17]:
cols = MID_STAR_UID.columns.tolist()

In [18]:
cols = ['MID','UID','STAR']

In [19]:
MID_STAR_UID = MID_STAR_UID[cols]

In [20]:
MID_STAR_UID

MID         UID  STAR
0       tt0111161   ur2509775    10
1       tt0111161   ur0997166    10
2       tt0111161   ur1005460     9
3       tt0111161   ur1898687    10
4       tt0111161   ur0094239     9
5       tt0111161   ur1285640     8
6       tt0111161   ur0611718    10
7       tt0111161   ur0257957    10
8       tt0111161   ur0355122    10
9       tt0111161   ur0842118    10
10      tt0111161  ur16117882    10
11      tt0111161   ur0174908    10
12      tt0111161   ur0265899    10
13      tt0111161  ur16161013    10
14      tt0111161   ur0226855     8
15      tt0111161   ur1003471    10
16      tt0111161   ur9365949    10
17      tt0111161  ur20345143    10
18      tt0111161   ur0043337    10
19      tt0111161   ur1532177     8
20      tt0111161  ur24573739    10
21      tt0111161   ur9871443    10
22      tt0111161   ur6657969     7
23      tt0111161  ur31182745    10
24      tt0111161  ur29409681    10
25      tt0111161   ur0138488     7
26      tt0111161   ur8635707    10
27      tt0111161   ur0082617     9
28      tt0111161  ur17447627    10
29      tt0111161   ur0643062     9
...           ...         ...   ...
205678  tt0169102   ur2498434     8
205679  tt0169102   ur1527854     8
205680  tt0169102   ur1119267    10
205681  tt0169102  ur15478585     4
205682  tt0169102  ur10948088     8
205683  tt0169102   ur4540074     7
205684  tt0169102   ur3518481     8
205685  tt0169102   ur0574035     8
205686  tt0169102   ur0912441     7
205687  tt0169102  ur12924719     1
205688  tt0169102  ur34567012     7
205689  tt0169102  ur10587962     6
205690  tt0169102   ur2366009     8
205691  tt0169102   ur0527288     4
205692  tt0169102   ur0391152     6
205693  tt0169102   ur0455012     3
205694  tt0169102   ur3600973     1
205695  tt0169102   ur1600076     4
205696  tt0169102   ur1228653     1
205697  tt0169102   ur3522562     5
205698  tt0169102   ur0305537     3
205699  tt0169102   ur1684817     2
205700  tt0169102   ur1928278     2
205701  tt0169102   ur0541597     2
205702  tt0169102   ur1351778     1
205703  tt0169102   ur0239428     3
205704  tt0169102   ur0945264     1
205705  tt0169102   ur1557088     1
205706  tt0169102   ur2081542     1
205707  tt0169102   ur1251318     1

[205708 rows x 3 columns]

In [21]:
###### concat MID_STAR_UID and MID_STAR_UID_EXT ########

In [25]:
MID_UID_STAR_COM = pd.concat([MID_STAR_UID,MID_STAR_UID_EXT],axis=0,ignore_index=True)

In [22]:
323171+205708

528879

In [26]:
MID_UID_STAR_COM

MID         UID  STAR
0       tt0111161   ur2509775    10
1       tt0111161   ur0997166    10
2       tt0111161   ur1005460     9
3       tt0111161   ur1898687    10
4       tt0111161   ur0094239     9
5       tt0111161   ur1285640     8
6       tt0111161   ur0611718    10
7       tt0111161   ur0257957    10
8       tt0111161   ur0355122    10
9       tt0111161   ur0842118    10
10      tt0111161  ur16117882    10
11      tt0111161   ur0174908    10
12      tt0111161   ur0265899    10
13      tt0111161  ur16161013    10
14      tt0111161   ur0226855     8
15      tt0111161   ur1003471    10
16      tt0111161   ur9365949    10
17      tt0111161  ur20345143    10
18      tt0111161   ur0043337    10
19      tt0111161   ur1532177     8
20      tt0111161  ur24573739    10
21      tt0111161   ur9871443    10
22      tt0111161   ur6657969     7
23      tt0111161  ur31182745    10
24      tt0111161  ur29409681    10
25      tt0111161   ur0138488     7
26      tt0111161   ur8635707    10
27      tt0111161   ur0082617     9
28      tt0111161  ur17447627    10
29      tt0111161   ur0643062     9
...           ...         ...   ...
528849  tt3498820  ur44261895     7
528850  tt3498820  ur66155439     8
528851  tt3498820  ur65968893     1
528852  tt3498820  ur63573225    10
528853  tt3498820   ur6141756     8
528854  tt3498820  ur66508300     8
528855  tt3498820  ur65144894     8
528856  tt3498820  ur54640256    10
528857  tt3498820   ur4535081     8
528858  tt3498820  ur48448272     8
528859  tt3498820  ur61514137    10
528860  tt3498820   ur6136793     9
528861  tt3498820  ur61675071     7
528862  tt3498820  ur65571567    10
528863  tt3498820  ur67378057    10
528864  tt3498820  ur67093391    10
528865  tt3498820  ur47346916     7
528866  tt3498820  ur24337173    10
528867  tt3498820  ur66474046     7
528868  tt3498820  ur65574658     5
528869  tt3498820  ur51120194     6
528870  tt3498820  ur66549718    10
528871  tt3498820  ur18648606     4
528872  tt3498820  ur66654441     1
528873  tt3498820  ur19781397     1
528874  tt3498820  ur47881457     1
528875  tt3498820  ur64382857     1
528876  tt3498820  ur66492584     1
528877  tt3498820  ur65995957     1
528878  tt3498820  ur66024302     1

[528879 rows x 3 columns]

In [27]:
MID_UID_STAR_COM.to_csv('MID_UID_STAR_COM.csv')

In [28]:
MID_UID_STAR_COM = pd.read_csv('MID_UID_STAR_COM.csv')

In [30]:
del MID_UID_STAR_COM['Unnamed: 0']

In [31]:
MID_UID_STAR_COM

MID         UID  STAR
0       tt0111161   ur2509775    10
1       tt0111161   ur0997166    10
2       tt0111161   ur1005460     9
3       tt0111161   ur1898687    10
4       tt0111161   ur0094239     9
5       tt0111161   ur1285640     8
6       tt0111161   ur0611718    10
7       tt0111161   ur0257957    10
8       tt0111161   ur0355122    10
9       tt0111161   ur0842118    10
10      tt0111161  ur16117882    10
11      tt0111161   ur0174908    10
12      tt0111161   ur0265899    10
13      tt0111161  ur16161013    10
14      tt0111161   ur0226855     8
15      tt0111161   ur1003471    10
16      tt0111161   ur9365949    10
17      tt0111161  ur20345143    10
18      tt0111161   ur0043337    10
19      tt0111161   ur1532177     8
20      tt0111161  ur24573739    10
21      tt0111161   ur9871443    10
22      tt0111161   ur6657969     7
23      tt0111161  ur31182745    10
24      tt0111161  ur29409681    10
25      tt0111161   ur0138488     7
26      tt0111161   ur8635707    10
27      tt0111161   ur0082617     9
28      tt0111161  ur17447627    10
29      tt0111161   ur0643062     9
...           ...         ...   ...
528849  tt3498820  ur44261895     7
528850  tt3498820  ur66155439     8
528851  tt3498820  ur65968893     1
528852  tt3498820  ur63573225    10
528853  tt3498820   ur6141756     8
528854  tt3498820  ur66508300     8
528855  tt3498820  ur65144894     8
528856  tt3498820  ur54640256    10
528857  tt3498820   ur4535081     8
528858  tt3498820  ur48448272     8
528859  tt3498820  ur61514137    10
528860  tt3498820   ur6136793     9
528861  tt3498820  ur61675071     7
528862  tt3498820  ur65571567    10
528863  tt3498820  ur67378057    10
528864  tt3498820  ur67093391    10
528865  tt3498820  ur47346916     7
528866  tt3498820  ur24337173    10
528867  tt3498820  ur66474046     7
528868  tt3498820  ur65574658     5
528869  tt3498820  ur51120194     6
528870  tt3498820  ur66549718    10
528871  tt3498820  ur18648606     4
528872  tt3498820  ur66654441     1
528873  tt3498820  ur19781397     1
528874  tt3498820  ur47881457     1
528875  tt3498820  ur64382857     1
528876  tt3498820  ur66492584     1
528877  tt3498820  ur65995957     1
528878  tt3498820  ur66024302     1

[528879 rows x 3 columns]

In [32]:
pivot_com = MID_UID_STAR_COM.pivot_table(values='STAR',index='UID',columns='MID')
pivot_com

MID        tt0012349  tt0015864  tt0017136  tt0017925  tt0018455  tt0019254  \
UID                                                                           
ur0000006        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000011        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000037        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000039        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000059        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000066        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000075        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000138        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000157        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000229        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000301        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000554        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000578        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000595        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000602        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000685        NaN        NaN        NaN        NaN        NaN        NaN   
ur0000917        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001071        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001107        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001165        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001220        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001246        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001379        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001529        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001586        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001593        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001713        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001757        NaN        NaN        NaN        NaN        NaN        NaN   
ur0001785        NaN        NaN        NaN        NaN        NaN        NaN   
ur0002216        NaN        NaN        NaN        NaN        NaN        NaN   
...              ...        ...        ...        ...        ...        ...   
ur9995807        NaN        NaN        NaN        NaN        NaN        NaN   
ur999582         NaN        NaN        NaN        NaN        NaN        NaN   
ur9996007        NaN        NaN        NaN        NaN        NaN        NaN   
ur999605         NaN        NaN        NaN        NaN        NaN        NaN   
ur9996202        NaN        NaN        NaN        NaN        NaN        NaN   
ur999666         NaN        NaN        NaN        NaN        NaN        NaN   
ur9996750        NaN        NaN        NaN        NaN        NaN        NaN   
ur9997193        NaN        NaN        NaN        NaN        NaN        NaN   
ur999736         NaN        NaN        NaN        NaN        NaN        NaN   
ur9997487        NaN        NaN        NaN        NaN        NaN        NaN   
ur9997555        NaN        NaN        NaN        NaN        NaN        NaN   
ur9997570        NaN        NaN        NaN        NaN        NaN        NaN   
ur9997592        NaN        NaN        NaN        NaN        NaN        NaN   
ur9997725        NaN        NaN        NaN        NaN        NaN        NaN   
ur9997788        NaN        NaN        NaN        NaN        NaN        NaN   
ur999795         NaN        NaN        NaN        NaN        NaN        NaN   
ur9998206        NaN        NaN        NaN        NaN        NaN        NaN   
ur9998274        NaN        NaN        NaN        

In [33]:
print "Number of reviews: " + str(len(MID_UID_STAR_COM))
print "Number of users: " + str(pivot_com.index.shape[0])
print "Number of movies: " + str(len(pivot_com.columns))

Number of reviews: 528879
Number of users: 254745
Number of movies: 481


In [34]:
pivot_com.to_csv('pivot_com.csv')


## Cosine similarity

In [35]:
df = pd.read_csv('pivot_com.csv',index_col='UID')
df.fillna(0,inplace=True)
df

tt0012349  tt0015864  tt0017136  tt0017925  tt0018455  tt0019254  \
UID                                                                           
ur0000006        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000011        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000037        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000039        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000059        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000066        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000075        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000138        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000157        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000229        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000301        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000554        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000578        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000595        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000602        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000685        0.0        0.0        0.0        0.0        0.0        0.0   
ur0000917        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001071        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001107        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001165        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001220        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001246        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001379        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001529        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001586        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001593        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001713        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001757        0.0        0.0        0.0        0.0        0.0        0.0   
ur0001785        0.0        0.0        0.0        0.0        0.0        0.0   
ur0002216        0.0        0.0        0.0        0.0        0.0        0.0   
...              ...        ...        ...        ...        ...        ...   
ur9995807        0.0        0.0        0.0        0.0        0.0        0.0   
ur999582         0.0        0.0        0.0        0.0        0.0        0.0   
ur9996007        0.0        0.0        0.0        0.0        0.0        0.0   
ur999605         0.0        0.0        0.0        0.0        0.0        0.0   
ur9996202        0.0        0.0        0.0        0.0        0.0        0.0   
ur999666         0.0        0.0        0.0        0.0        0.0        0.0   
ur9996750        0.0        0.0        0.0        0.0        0.0        0.0   
ur9997193        0.0        0.0        0.0        0.0        0.0        0.0   
ur999736         0.0        0.0        0.0        0.0        0.0        0.0   
ur9997487        0.0        0.0        0.0        0.0        0.0        0.0   
ur9997555        0.0        0.0        0.0        0.0        0.0        0.0   
ur9997570        0.0        0.0        0.0        0.0        0.0        0.0   
ur9997592        0.0        0.0        0.0        0.0        0.0        0.0   
ur9997725        0.0        0.0        0.0        0.0        0.0        0.0   
ur9997788        0.0        0.0        0.0        0.0        0.0        0.0   
ur999795         0.0        0.0        0.0        0.0        0.0        0.0   
ur9998206        0.0        0.0        0.0        0.0        0.0        0.0   
ur9998274        0.0        0.0        0.0        0.0        

In [42]:
df_bigger_100 = df[df.sum(axis=1)>100]
df_bigger_100

tt0012349  tt0015864  tt0017136  tt0017925  tt0018455  tt0019254  \
UID                                                                           
ur0002746        0.0        0.0        0.0        0.0        0.0        0.0   
ur0003136        0.0        7.0        0.0        0.0        0.0        0.0   
ur0011596        0.0        0.0        0.0        0.0        0.0        0.0   
ur0011762        0.0        0.0        0.0        7.0        0.0        7.0   
ur0018365        0.0        0.0        0.0        0.0        0.0        0.0   
ur0020866        0.0        0.0        8.0        0.0        0.0        0.0   
ur0023796        0.0        0.0        0.0        0.0        0.0        0.0   
ur0024463        0.0        0.0        0.0        0.0        0.0        0.0   
ur0033913        0.0        0.0        0.0        0.0        0.0        0.0   
ur0035229        0.0        0.0       10.0        0.0       10.0        0.0   
ur0035842        0.0        0.0        0.0        0.0        0.0        0.0   
ur0041958        0.0        0.0        0.0        0.0        0.0        0.0   
ur0063241        0.0        0.0        0.0        0.0        0.0        0.0   
ur0064493        0.0        0.0        0.0        0.0        0.0        0.0   
ur0064529        0.0        0.0        0.0        0.0        0.0        0.0   
ur0068788        0.0        0.0        0.0        0.0        0.0       10.0   
ur0070535        0.0        0.0        0.0        0.0        0.0        0.0   
ur0073800        0.0        0.0        0.0        0.0        0.0        0.0   
ur0075285        0.0        0.0        0.0        0.0        0.0        0.0   
ur0079652        0.0        0.0        0.0       10.0        0.0        0.0   
ur0079850        0.0        0.0        0.0        0.0        0.0        0.0   
ur0088076        0.0        0.0        0.0        0.0        0.0        0.0   
ur0089164        0.0        0.0        0.0        0.0        0.0        0.0   
ur0090091        0.0        0.0        0.0        0.0        0.0        0.0   
ur0090767        0.0        0.0        0.0        0.0        0.0        0.0   
ur0092583        0.0        0.0        0.0        0.0        8.0        0.0   
ur0094501        0.0        0.0        0.0        0.0        0.0        0.0   
ur0095587        0.0        0.0        0.0        0.0        0.0        0.0   
ur0099933        0.0        0.0        0.0        0.0        0.0        0.0   
ur0100620        0.0        0.0        0.0        0.0        0.0        0.0   
...              ...        ...        ...        ...        ...        ...   
ur9521536        0.0        0.0        0.0        0.0        0.0        0.0   
ur9557126        0.0        0.0        0.0        0.0        0.0        0.0   
ur9605           0.0        0.0        0.0        0.0        0.0        0.0   
ur9619380        0.0        0.0        0.0        0.0        0.0        0.0   
ur963478         0.0        0.0        0.0        0.0        0.0        0.0   
ur965252         0.0        0.0        0.0        0.0        0.0        0.0   
ur968128         0.0        0.0        0.0        0.0        0.0        0.0   
ur968914         0.0        0.0        0.0        0.0        0.0        0.0   
ur9705007        0.0        0.0        0.0        0.0        0.0        0.0   
ur970606         0.0        0.0        0.0        0.0        0.0        0.0   
ur9725326        0.0        0.0        0.0        0.0        0.0        0.0   
ur972645         0.0        0.0        0.0        0.0        0.0        0.0   
ur975530         0.0        0.0        0.0        0.0        0.0        0.0   
ur9777631        0.0        0.0        0.0        0.0        0.0        0.0   
ur9780741        0.0        0.0        0.0        0.0        0.0        0.0   
ur9814911        0.0        0.0        0.0        0.0        0.0        0.0   
ur9818977        0.0        0.0        0.0        0.0        0.0        0.0   
ur9865518        0.0        0.0        0.0        0.0        

In [43]:
df_bigger_100 = df_bigger_100.unstack().reset_index(name='value')

In [45]:
# all stars including 0 from 2742 users
df_bigger_100

level_0        UID  value
0        tt0012349  ur0002746    0.0
1        tt0012349  ur0003136    0.0
2        tt0012349  ur0011596    0.0
3        tt0012349  ur0011762    0.0
4        tt0012349  ur0018365    0.0
5        tt0012349  ur0020866    0.0
6        tt0012349  ur0023796    0.0
7        tt0012349  ur0024463    0.0
8        tt0012349  ur0033913    0.0
9        tt0012349  ur0035229    0.0
10       tt0012349  ur0035842    0.0
11       tt0012349  ur0041958    0.0
12       tt0012349  ur0063241    0.0
13       tt0012349  ur0064493    0.0
14       tt0012349  ur0064529    0.0
15       tt0012349  ur0068788    0.0
16       tt0012349  ur0070535    0.0
17       tt0012349  ur0073800    0.0
18       tt0012349  ur0075285    0.0
19       tt0012349  ur0079652    0.0
20       tt0012349  ur0079850    0.0
21       tt0012349  ur0088076    0.0
22       tt0012349  ur0089164    0.0
23       tt0012349  ur0090091    0.0
24       tt0012349  ur0090767    0.0
25       tt0012349  ur0092583    0.0
26       tt0012349  ur0094501    0.0
27       tt0012349  ur0095587    0.0
28       tt0012349  ur0099933    0.0
29       tt0012349  ur0100620    0.0
...            ...        ...    ...
1318872  tt3659388  ur9521536    0.0
1318873  tt3659388  ur9557126    0.0
1318874  tt3659388     ur9605    0.0
1318875  tt3659388  ur9619380    0.0
1318876  tt3659388   ur963478    0.0
1318877  tt3659388   ur965252    0.0
1318878  tt3659388   ur968128    0.0
1318879  tt3659388   ur968914    0.0
1318880  tt3659388  ur9705007    0.0
1318881  tt3659388   ur970606    0.0
1318882  tt3659388  ur9725326    0.0
1318883  tt3659388   ur972645    0.0
1318884  tt3659388   ur975530    0.0
1318885  tt3659388  ur9777631    0.0
1318886  tt3659388  ur9780741    0.0
1318887  tt3659388  ur9814911    0.0
1318888  tt3659388  ur9818977    0.0
1318889  tt3659388  ur9865518    0.0
1318890  tt3659388   ur989035    0.0
1318891  tt3659388    ur99112    0.0
1318892  tt3659388  ur9915063    0.0
1318893  tt3659388  ur9917850    0.0
1318894  tt3659388  ur9927446    0.0
1318895  tt3659388  ur9927546    8.0
1318896  tt3659388  ur9938570    0.0
1318897  tt3659388  ur9944312    0.0
1318898  tt3659388  ur9956214    0.0
1318899  tt3659388  ur9964186    0.0
1318900  tt3659388  ur9972457    0.0
1318901  tt3659388  ur9987799    0.0

[1318902 rows x 3 columns]

In [46]:
2742*481

1318902

In [47]:
# delete all 0 stars
df = df_bigger_100[df_bigger_100['value'] != 0]

In [49]:
df = df.reset_index(drop=True)

In [50]:
df.columns = ['MID','UID','value']

In [51]:
df

MID         UID  value
0       tt0012349   ur0137908    8.0
1       tt0012349   ur0222418    8.0
2       tt0012349   ur0453068   10.0
3       tt0012349   ur0562732   10.0
4       tt0012349   ur0819382    8.0
5       tt0012349   ur0826090    8.0
6       tt0012349   ur0850869   10.0
7       tt0012349  ur10334028    8.0
8       tt0012349  ur10962105    9.0
9       tt0012349   ur1174211    8.0
10      tt0012349   ur1234929    8.0
11      tt0012349  ur13017201    8.0
12      tt0012349  ur13134536    8.0
13      tt0012349  ur13566917    8.0
14      tt0012349   ur1384699    8.0
15      tt0012349  ur15562504    8.0
16      tt0012349  ur17029428   10.0
17      tt0012349  ur17699578    5.0
18      tt0012349  ur18876660    9.0
19      tt0012349  ur19257379   10.0
20      tt0012349  ur19574884    9.0
21      tt0012349  ur19783225    7.0
22      tt0012349   ur1994077    9.0
23      tt0012349  ur20018357    8.0
24      tt0012349  ur20552756    9.0
25      tt0012349  ur20597997    9.0
26      tt0012349  ur20815663    8.0
27      tt0012349  ur22131361   10.0
28      tt0012349  ur23853088   10.0
29      tt0012349   ur2467618    6.0
...           ...         ...    ...
104938  tt3659388  ur60028700    8.0
104939  tt3659388  ur60052163    8.0
104940  tt3659388  ur60255714    9.0
104941  tt3659388  ur60376752    9.0
104942  tt3659388  ur60603286   10.0
104943  tt3659388  ur61067348    8.0
104944  tt3659388  ur61244584    8.0
104945  tt3659388   ur6134663    7.0
104946  tt3659388   ur6136793   10.0
104947  tt3659388   ur6141756    6.0
104948  tt3659388  ur61431381    6.0
104949  tt3659388  ur61541609   10.0
104950  tt3659388  ur61617922    9.0
104951  tt3659388  ur61780321   10.0
104952  tt3659388   ur6216723    9.0
104953  tt3659388  ur62906690    9.0
104954  tt3659388  ur62910059    7.0
104955  tt3659388  ur63827208    9.0
104956  tt3659388   ur6458242    2.0
104957  tt3659388  ur64793543    8.0
104958  tt3659388  ur64848949    9.0
104959  tt3659388  ur65144138   10.0
104960  tt3659388  ur65256868   10.0
104961  tt3659388  ur65741743    9.0
104962  tt3659388  ur66355076    7.0
104963  tt3659388   ur7813355    8.0
104964  tt3659388   ur8462477    8.0
104965  tt3659388   ur8503729    9.0
104966  tt3659388   ur8546957    5.0
104967  tt3659388   ur9927546    8.0

[104968 rows x 3 columns]

In [54]:
df['UID'].unique().shape[0]

2742

In [56]:
print "Number of reviews: " + str(len(df))
print "Number of users: " + str(df['UID'].unique().shape[0])
print "Number of movies: " + str(df['MID'].unique().shape[0])

Number of reviews: 104968
Number of users: 2742
Number of movies: 481


In [66]:
# Movie Menu

movie_menu = pd.DataFrame({'MID': df['MID'].unique().tolist(),
                          'Code': np.arange(1,482)})

In [67]:
movie_menu

Code        MID
0       1  tt0012349
1       2  tt0015864
2       3  tt0017136
3       4  tt0017925
4       5  tt0018455
5       6  tt0019254
6       7  tt0021749
7       8  tt0022100
8       9  tt0025316
9      10  tt0027977
10     11  tt0031381
11     12  tt0031679
12     13  tt0032138
13     14  tt0032551
14     15  tt0032553
15     16  tt0032976
16     17  tt0033467
17     18  tt0033870
18     19  tt0034583
19     20  tt0036775
20     21  tt0036868
21     22  tt0038650
22     23  tt0040522
23     24  tt0040897
24     25  tt0041546
25     26  tt0041959
26     27  tt0042192
27     28  tt0042876
28     29  tt0043014
29     30  tt0044079
..    ...        ...
451   452  tt1895587
452   453  tt1954470
453   454  tt1959490
454   455  tt1979320
455   456  tt2015381
456   457  tt2024544
457   458  tt2084970
458   459  tt2096673
459   460  tt2106476
460   461  tt2109248
461   462  tt2179136
462   463  tt2267998
463   464  tt2278388
464   465  tt2294629
465   466  tt2310332
466   467  tt2322441
467   468  tt2379713
468   469  tt2395427
469   470  tt2488496
470   471  tt2562232
471   472  tt2582802
472   473  tt2788710
473   474  tt2872732
474   475  tt2948356
475   476  tt2975590
476   477  tt3011894
477   478  tt3170832
478   479  tt3460252
479   480  tt3498820
480   481  tt3659388

[481 rows x 2 columns]

In [63]:
len(df['UID'].unique().tolist())

2742

In [ ]:
# User menu

In [107]:
uid_unique = df['UID'].unique().tolist()
uid_unique_sort = sorted(uid_unique)

In [111]:
uid_unique

['ur0137908',
 'ur0222418',
 'ur0453068',
 'ur0562732',
 'ur0819382',
 'ur0826090',
 'ur0850869',
 'ur10334028',
 'ur10962105',
 'ur1174211',
 'ur1234929',
 'ur13017201',
 'ur13134536',
 'ur13566917',
 'ur1384699',
 'ur15562504',
 'ur17029428',
 'ur17699578',
 'ur18876660',
 'ur19257379',
 'ur19574884',
 'ur19783225',
 'ur1994077',
 'ur20018357',
 'ur20552756',
 'ur20597997',
 'ur20815663',
 'ur22131361',
 'ur23853088',
 'ur2467618',
 'ur2483625',
 'ur2514416',
 'ur25845421',
 'ur26443691',
 'ur2707735',
 'ur28071275',
 'ur2860723',
 'ur2898520',
 'ur3063013',
 'ur31527914',
 'ur3212364',
 'ur3270789',
 'ur33697153',
 'ur34049683',
 'ur34967775',
 'ur39479451',
 'ur39517558',
 'ur4067661',
 'ur4234119',
 'ur4248714',
 'ur4405474',
 'ur4445210',
 'ur4693077',
 'ur47006221',
 'ur4838150',
 'ur4888011',
 'ur5037232',
 'ur5291991',
 'ur5560976',
 'ur56393956',
 'ur60028700',
 'ur6625713',
 'ur67651029',
 'ur7484735',
 'ur9938570',
 'ur9972457',
 'ur9987799',
 'ur0003136',
 'ur0176092',
 'u

In [110]:
uid_unique_sort

['ur0002746',
 'ur0003136',
 'ur0011596',
 'ur0011762',
 'ur0018365',
 'ur0020866',
 'ur0023796',
 'ur0024463',
 'ur0033913',
 'ur0035229',
 'ur0035842',
 'ur0041958',
 'ur0063241',
 'ur0064493',
 'ur0064529',
 'ur0068788',
 'ur0070535',
 'ur0073800',
 'ur0075285',
 'ur0079652',
 'ur0079850',
 'ur0088076',
 'ur0089164',
 'ur0090091',
 'ur0090767',
 'ur0092583',
 'ur0094501',
 'ur0095587',
 'ur0099933',
 'ur0100620',
 'ur0100964',
 'ur0102816',
 'ur0105696',
 'ur0111563',
 'ur0111731',
 'ur0116181',
 'ur0119489',
 'ur0121336',
 'ur0123856',
 'ur0128216',
 'ur0135721',
 'ur0135863',
 'ur0137908',
 'ur0139258',
 'ur0140921',
 'ur0144911',
 'ur0146370',
 'ur0150331',
 'ur0152704',
 'ur0153547',
 'ur0154317',
 'ur0157498',
 'ur0158253',
 'ur0165374',
 'ur0166205',
 'ur0166317',
 'ur0167590',
 'ur0167865',
 'ur0171876',
 'ur0172654',
 'ur0174609',
 'ur0176092',
 'ur0178741',
 'ur0179443',
 'ur0182733',
 'ur0185160',
 'ur0186091',
 'ur0187170',
 'ur0187171',
 'ur0191545',
 'ur0193491',
 'ur01

In [113]:
user_menu = pd.DataFrame({'UID': uid_unique_sort,
                          'Code': np.arange(1,2743)})

In [114]:
user_menu

Code        UID
0        1  ur0002746
1        2  ur0003136
2        3  ur0011596
3        4  ur0011762
4        5  ur0018365
5        6  ur0020866
6        7  ur0023796
7        8  ur0024463
8        9  ur0033913
9       10  ur0035229
10      11  ur0035842
11      12  ur0041958
12      13  ur0063241
13      14  ur0064493
14      15  ur0064529
15      16  ur0068788
16      17  ur0070535
17      18  ur0073800
18      19  ur0075285
19      20  ur0079652
20      21  ur0079850
21      22  ur0088076
22      23  ur0089164
23      24  ur0090091
24      25  ur0090767
25      26  ur0092583
26      27  ur0094501
27      28  ur0095587
28      29  ur0099933
29      30  ur0100620
...    ...        ...
2712  2713  ur9521536
2713  2714  ur9557126
2714  2715     ur9605
2715  2716  ur9619380
2716  2717   ur963478
2717  2718   ur965252
2718  2719   ur968128
2719  2720   ur968914
2720  2721  ur9705007
2721  2722   ur970606
2722  2723  ur9725326
2723  2724   ur972645
2724  2725   ur975530
2725  2726  ur9777631
2726  2727  ur9780741
2727  2728  ur9814911
2728  2729  ur9818977
2729  2730  ur9865518
2730  2731   ur989035
2731  2732    ur99112
2732  2733  ur9915063
2733  2734  ur9917850
2734  2735  ur9927446
2735  2736  ur9927546
2736  2737  ur9938570
2737  2738  ur9944312
2738  2739  ur9956214
2739  2740  ur9964186
2740  2741  ur9972457
2741  2742  ur9987799

[2742 rows x 2 columns]

In [118]:
# To create sequence table
user_code = []
for i in df['UID']:
    user_code.append(user_menu['UID'].tolist().index(i)+1)

In [119]:
len(user_code)

104968

In [120]:
movie_code = []
for i in df['MID']:
    movie_code.append(movie_menu['MID'].tolist().index(i)+1)

In [121]:
len(movie_code)

104968

In [122]:
seq_100 = pd.DataFrame({'MID': movie_code,
                        "UID": user_code,
                        'STAR': df['value']
                       })

In [123]:
seq_100

MID  STAR   UID
0         1   8.0    43
1         1   8.0    82
2         1  10.0   166
3         1  10.0   197
4         1   8.0   266
5         1   8.0   270
6         1  10.0   275
7         1   8.0   324
8         1   9.0   392
9         1   8.0   467
10        1   8.0   530
11        1   8.0   581
12        1   8.0   594
13        1   8.0   619
14        1   8.0   634
15        1   8.0   767
16        1  10.0   904
17        1   5.0   950
18        1   9.0  1023
19        1  10.0  1048
20        1   9.0  1075
21        1   7.0  1097
22        1   9.0  1116
23        1   8.0  1128
24        1   9.0  1169
25        1   9.0  1173
26        1   8.0  1192
27        1  10.0  1282
28        1  10.0  1411
29        1   6.0  1460
...     ...   ...   ...
104938  481   8.0  2422
104939  481   8.0  2423
104940  481   9.0  2426
104941  481   9.0  2427
104942  481  10.0  2431
104943  481   8.0  2438
104944  481   8.0  2441
104945  481   7.0  2442
104946  481  10.0  2443
104947  481   6.0  2444
104948  481   6.0  2445
104949  481  10.0  2446
104950  481   9.0  2449
104951  481  10.0  2450
104952  481   9.0  2453
104953  481   9.0  2461
104954  481   7.0  2462
104955  481   9.0  2472
104956  481   2.0  2482
104957  481   8.0  2485
104958  481   9.0  2486
104959  481  10.0  2491
104960  481  10.0  2492
104961  481   9.0  2502
104962  481   7.0  2510
104963  481   8.0  2596
104964  481   8.0  2645
104965  481   9.0  2647
104966  481   5.0  2650
104967  481   8.0  2736

[104968 rows x 3 columns]

In [124]:
seq_100.to_csv('seq_100.csv')

In [130]:
df = pd.read_csv('seq_100.csv')

In [131]:
del df['Unnamed: 0']

In [132]:
df

MID  STAR   UID
0         1   8.0    43
1         1   8.0    82
2         1  10.0   166
3         1  10.0   197
4         1   8.0   266
5         1   8.0   270
6         1  10.0   275
7         1   8.0   324
8         1   9.0   392
9         1   8.0   467
10        1   8.0   530
11        1   8.0   581
12        1   8.0   594
13        1   8.0   619
14        1   8.0   634
15        1   8.0   767
16        1  10.0   904
17        1   5.0   950
18        1   9.0  1023
19        1  10.0  1048
20        1   9.0  1075
21        1   7.0  1097
22        1   9.0  1116
23        1   8.0  1128
24        1   9.0  1169
25        1   9.0  1173
26        1   8.0  1192
27        1  10.0  1282
28        1  10.0  1411
29        1   6.0  1460
...     ...   ...   ...
104938  481   8.0  2422
104939  481   8.0  2423
104940  481   9.0  2426
104941  481   9.0  2427
104942  481  10.0  2431
104943  481   8.0  2438
104944  481   8.0  2441
104945  481   7.0  2442
104946  481  10.0  2443
104947  481   6.0  2444
104948  481   6.0  2445
104949  481  10.0  2446
104950  481   9.0  2449
104951  481  10.0  2450
104952  481   9.0  2453
104953  481   9.0  2461
104954  481   7.0  2462
104955  481   9.0  2472
104956  481   2.0  2482
104957  481   8.0  2485
104958  481   9.0  2486
104959  481  10.0  2491
104960  481  10.0  2492
104961  481   9.0  2502
104962  481   7.0  2510
104963  481   8.0  2596
104964  481   8.0  2645
104965  481   9.0  2647
104966  481   5.0  2650
104967  481   8.0  2736

[104968 rows x 3 columns]

In [133]:
print "Unique movie: " + str(df['MID'].unique().shape[0])
print "Unique user: " + str(df['UID'].unique().shape[0])
print "length of dataset: " + str(len(df)) 

Unique movie: 481
Unique user: 2742
length of dataset: 104968


In [173]:
#Change star scale from 1-10 to 1-5
rating = []
for i in df["STAR"]:
    if i == 10.0:
        rating.append(5)
    if i == 9.0:
        rating.append(4.5)
    if i == 8.0:
        rating.append(4)
    if i == 7.0:
        rating.append(3.5)
    if i == 6.0:
        rating.append(3)
    if i == 5.0:
        rating.append(2.5)
    if i == 4.0:
        rating.append(2)
    if i == 3.0:
        rating.append(1.5)
    if i == 2.0:
        rating.append(1)
    if i == 1.0:
        rating.append(0.5)

In [174]:
df['Rating'] = rating
del df['STAR']
df

MID   UID  Rating
0         1    43     4.0
1         1    82     4.0
2         1   166     5.0
3         1   197     5.0
4         1   266     4.0
5         1   270     4.0
6         1   275     5.0
7         1   324     4.0
8         1   392     4.5
9         1   467     4.0
10        1   530     4.0
11        1   581     4.0
12        1   594     4.0
13        1   619     4.0
14        1   634     4.0
15        1   767     4.0
16        1   904     5.0
17        1   950     2.5
18        1  1023     4.5
19        1  1048     5.0
20        1  1075     4.5
21        1  1097     3.5
22        1  1116     4.5
23        1  1128     4.0
24        1  1169     4.5
25        1  1173     4.5
26        1  1192     4.0
27        1  1282     5.0
28        1  1411     5.0
29        1  1460     3.0
...     ...   ...     ...
104938  481  2422     4.0
104939  481  2423     4.0
104940  481  2426     4.5
104941  481  2427     4.5
104942  481  2431     5.0
104943  481  2438     4.0
104944  481  2441     4.0
104945  481  2442     3.5
104946  481  2443     5.0
104947  481  2444     3.0
104948  481  2445     3.0
104949  481  2446     5.0
104950  481  2449     4.5
104951  481  2450     5.0
104952  481  2453     4.5
104953  481  2461     4.5
104954  481  2462     3.5
104955  481  2472     4.5
104956  481  2482     1.0
104957  481  2485     4.0
104958  481  2486     4.5
104959  481  2491     5.0
104960  481  2492     5.0
104961  481  2502     4.5
104962  481  2510     3.5
104963  481  2596     4.0
104964  481  2645     4.0
104965  481  2647     4.5
104966  481  2650     2.5
104967  481  2736     4.0

[104968 rows x 3 columns]

In [175]:
n_users = df.UID.unique().shape[0]

n_items = df.MID.unique().shape[0]

print 'Number of users = ' + str(n_users) + ' | Number of movies = ' + str(n_items)

Number of users = 2742 | Number of movies = 481


In [222]:
from sklearn import cross_validation as cv

train_data,test_data = cv.train_test_split(df, test_size = 0.25,random_state = 42)

In [242]:
train_data

MID   UID  Rating
49816   242   659     3.5
60966   293  1445     4.5
84049   381  2425     2.5
2528     19  1328     5.0
60657   291  1633     4.5
34335   177  1006     5.0
95810   435  2021     0.5
43242   211  2351     2.5
19453   108  1748     4.5
49750   241  2553     2.5
79038   364  2688     3.0
100789  462  1003     3.0
38348   190  2156     4.0
98253   447  1476     5.0
10039    69   879     5.0
98498   449   669     4.0
43936   215   911     4.0
81154   371  2408     4.0
83296   379  1921     3.5
66100   312  1808     4.5
102626  470  1127     3.0
39778   196  2710     5.0
27249   144   924     4.0
54229   262  1135     2.5
53845   260  1815     4.5
92953   425   298     4.5
82840   378   909     2.0
77825   359  1345     3.5
38595   192   432     5.0
95238   433  1996     4.5
...     ...   ...     ...
25658   138  1377     4.0
93016   425   879     0.5
71932   335  1757     3.5
28693   151   805     3.0
85305   386  1354     3.0
53707   259  2235     3.5
83104   378  2426     4.0
104724  481   619     4.0
103355  473   617     2.5
5311     39  1866     4.5
67969   320  1255     5.0
64925   309   304     2.5
62955   301  1099     4.0
59735   286  1249     5.0
769       9   275     5.0
64820   308  1630     3.5
67221   317  1814     3.0
41090   202   244     3.5
16023    93   922     4.5
60263   289  2518     4.5
44131   216  1293     3.5
87498   396  2191     1.5
37194   186  1256     4.0
82386   375  2367     1.5
6265     45  2483     4.5
54886   265  1921     3.5
76820   354   705     3.5
103694  475   160     4.0
860       9  2742     3.0
15795    92  1952     5.0

[78726 rows x 3 columns]

In [223]:
for line in train_data.itertuples():
    print line
    break

Pandas(Index=49816, MID=242, UID=659, Rating=3.5)


In [224]:
train_data_matrix = np.zeros((n_users,n_items))
for line in train_data.itertuples():
    train_data_matrix[line[2]-1, line[1]-1] = line[3]

In [225]:
test_data_matrix = np.zeros((n_users, n_items))

for line in test_data.itertuples():
    test_data_matrix[line[2]-1, line[1]-1] = line[3]

In [226]:
from sklearn.metrics.pairwise import pairwise_distances

user_similarity = pairwise_distances(train_data_matrix, metric = "cosine")

item_similarity = pairwise_distances(train_data_matrix.T, metric = "cosine")

In [227]:
user_similarity.shape

(2742, 2742)

In [228]:
item_similarity.shape

(481, 481)

In [229]:
def predict(rating, similarity, type = 'user'):

    if type == 'user':

        mean_user_rating = rating.mean(axis = 1)

        rating_diff = (rating - mean_user_rating[:,np.newaxis])

        pred = mean_user_rating[:,np.newaxis] + similarity.dot(rating_diff) / np.array([np.abs(similarity).sum(axis=1)]).T

    elif type == 'item':

        pred = rating.dot(similarity) / np.array([np.abs(similarity).sum(axis=1)])

    return pred

In [230]:
item_prediction = predict(train_data_matrix, item_similarity, type = 'item')

user_prediction = predict(train_data_matrix, user_similarity, type = 'user')

In [231]:
from sklearn.metrics import mean_squared_error

from math import sqrt

def rmse(prediction, ground_truth):

    prediction = prediction[ground_truth.nonzero()].flatten()

    ground_truth = ground_truth[ground_truth.nonzero()].flatten()

    return sqrt(mean_squared_error(prediction, ground_truth))

In [238]:
print 'User based CF RMSE: ' + str(rmse(user_prediction, test_data_matrix))

print 'Item based CF RMSE: ' + str(rmse(item_prediction, test_data_matrix))

User based CF RMSE: 3.4893905315
Item based CF RMSE: 3.54433951417


In [239]:
import scipy.sparse as sp
from scipy.sparse.linalg import svds

    #get SVD components from train matrix. Choose k.
u, s, vt = svds(train_data_matrix,k=20)
s_diag_matrix=np.diag(s)
X_pred = np.dot(np.dot(u, s_diag_matrix), vt)

print 'User-based CF MSE: ' + str(rmse(X_pred, test_data_matrix))

User-based CF MSE: 3.1187908232


In [234]:
ratings = np.zeros((n_users, n_items))
for row in df.itertuples():
    ratings[row[2]-1, row[1]-1] = row[3]
ratings

array([[ 0. ,  0. ,  0. , ...,  0. ,  0. ,  0. ],
       [ 0. ,  3.5,  0. , ...,  0. ,  0. ,  0. ],
       [ 0. ,  0. ,  0. , ...,  0. ,  0. ,  0. ],
       ..., 
       [ 0. ,  0. ,  0. , ...,  0. ,  0. ,  0. ],
       [ 4. ,  0. ,  4. , ...,  0. ,  0. ,  0. ],
       [ 4.5,  5. ,  0. , ...,  0. ,  0. ,  0. ]])

In [235]:
ratings.nonzero()

(array([   0,    0,    0, ..., 2741, 2741, 2741]),
 array([ 21,  48,  71, ..., 208, 211, 224]))

In [236]:
sparsity = float(len(ratings.nonzero()[0]))
sparsity /= (ratings.shape[0] * ratings.shape[1])
sparsity *= 100
print 'Sparsity: {:4.2f}%'.format(sparsity)

Sparsity: 7.96%


In [252]:
import nltk.classify.util
from nltk.classify import NaiveBayesClassifier
from nltk.corpus import movie_reviews